<p style="font-size:200%; font-weight:bold"> Layer One</p>

- Author: Yichen Luo
- Date: 20220822

In [78]:
import pandas as pd
import requests
import time
import os
import datetime
import re
from web3 import Web3
from hexbytes import HexBytes

from IPython.core.interactiveshell import InteractiveShell
pd.set_option('max_colwidth', 100)
pd.set_option('display.max_columns', 100)

RD = '/home/team_defi/02_rdata/'
WD = '/home/team_defi/03_wdata/'
RES = '/home/team_defi/04_result/'
InteractiveShell.ast_node_interactivity = 'all'

# Root Account

In [89]:
# dfs = []
# chains = ['ethereum', 'binance', 'avalanche', 'fantom', 'polygon']

# for chain in chains:
#     df = pd.read_csv(f'/home/yichen/team_defi/04_result/insider_trading/root_list/root_list_final/root_{chain}.csv')
#     df['chain'] = chain
#     dfs.append(df)

# dfs = pd.concat(dfs)
# dfs['normal_token'] = -1
# dfs['nft_token'] = -1

# dfs
# dfs.to_csv(f'{WD}/connected_wallet/list_from/root_list.csv', index=False)

root       tokenName tokenSymbol  \
0   0x742025b32fdda654df1aa5ae348928331ff05062        Callisto       C3000   
1   0xef0121d57d9e4324c3de83cf2a686ff5ac13c3a4        Callisto       C3000   
2   0xa625141e73ab1af1b57efbbad9ba9ab8813393e3            SYNC        SYNC   
3   0x6e86c831b85cc37f0aeeb5d553c40b257af8fb42  t.me/skin_port    SKINPORT   
4   0x72969afa049fa40e808d42f807ef4640a7cac5ec    KING VITALIK   KING ????   
..                                         ...             ...         ...   
24  0x4dbe648f797e7ec51da3eae23a89b971b4e022a5     Chihiro Inu       CHIRO   
25  0x5a6dc942826807539ca19d21c132e4b004075de0  NextEarthToken        NXTT   
26  0x3030f09fe7ea8fa6762c13d12afa8541cb2c6644          Dogioh         DGH   
27  0x81411b800dcc935e1aaf0ed01dd1c0777236153c            POKI        POKI   
28  0xadc42c844b8392ca353e079030609b6303d7f51d            Poge        Poge   

                               contractAddress     chain  normal_token  \
0   0x2a15de7c821baa1a727039b76d540b36b23db257  ethereum            -1   
1   0xa0fd12272cc4da86aebf9d592cdad253cbbc25fb  ethereum            -1   
2   0xb6ff96b8a8d214544ca0dbc9b33f7ad6503efd32  ethereum            -1   
3   0x506d62bf7d8a8f444f13533081dc03470483f4ea  ethereum            -1   
4   0xcbfb937a75f8baf9d94e064cc90b1c045f7c25fa  ethereum            -1   
..                                         ...       ...           ...   
24  0x35156b404C3f9bdaf45ab65Ba315419bcDe3775c   polygon            -1   
25  0x0d0B8488222F7f83B23E365320a4021b12eAD608   polygon            -1   
26  0x87842eD511C255a06aE872E7Ad83a64a1e3bD39c   polygon            -1   
27  0x3E41CE4f7ef7ca7C23640d2C8a906552a2A90092   polygon            -1   
28  0x6EA856c7A96d7366De2bbB600B956617d344DDa4   polygon            -1   

    nft_token  
0          -1  
1          -1  
2          -1  
3          -1  
4          -1  
..        ...  
24         -1  
25         -1  
26         -1  
27         -1  
28         -1  

[14807 rows x 7 columns]

# Transaction

## Search

### To

In [ ]:
dfs = pd.read_csv(f'{WD}/connected_wallet/list/root_list.csv')

done = dfs.loc[(dfs['normal_token'] != -1)&(dfs['nft_token'] != -1)].shape[0]
total = dfs.shape[0]
    
for idx, row in dfs.loc[(dfs['normal_token'] == -1)|(dfs['nft_token'] == -1)].iterrows():
    done += 1
    root = row['root']
    chain = row['chain']
    tokenName = row['tokenName']
    tokenSymbol = row['tokenSymbol']
    
    lst = pd.read_csv(f'{RD}connected_accounts/list/root_{chain}_list.csv')
    
    try:
        
        for token_type in ['normal_token', 'nft_token']:
            if lst.loc[lst['root'] == root, token_type].values[0] == 0: 
                dfs.loc[(dfs['root'] == root)&(dfs['chain'] == chain), token_type] = 0
                dfs.to_csv(f'{WD}/connected_wallet/list/root_list.csv', index=False)
                print(f'{tokenSymbol} no {token_type}')
                continue

            df = pd.read_csv(f'{RD}connected_accounts/csv/{root}_{chain}_{token_type}.csv')
            # Transfer out of the Address
            df = df.loc[df['from'] == root]

            # Home Token
            df = df.loc[(df['tokenName'] == tokenName)&(df['tokenSymbol'] == tokenSymbol)]

            # Not Team Finance
            if chain == 'ethereum': 
                df = df.loc[df['to'] != '0xe2fe530c047f2d85298b07d9333c05737f1435fb']
                rpc = 'https://rpc.ankr.com/eth'

            if chain == 'binance': 
                df = df.loc[df['to'] != '0x0c89c0407775dd89b12918b9c0aa42bf96518820']
                rpc = 'https://bscrpc.com'

            if chain == 'avalanche': 
                df = df.loc[df['to'] != '0xe2fe530c047f2d85298b07d9333c05737f1435fb']
                rpc = 'https://api.avax.network/ext/bc/C/rpc'

            if chain == 'fantom': 
                df = df.loc[df['to'] != '0x9f726019452d65a120e1f7ae6b937ee9ebd72440']
                rpc = 'https://rpc.ftm.tools'

            if chain == 'polygon': 
                df = df.loc[df['to'] != '0x3ef7442df454ba6b7c1deec8ddf29cfb2d6e56c7']
                rpc = 'https://polygon-rpc.com'   

            # Not Burn Address
            df = df.loc[(df['to']!= '0x0000000000000000000000000000000000000000')&
                        (df['to']!= '0x000000000000000000000000000000000000dead')
                       ]

            # Not Contract
            for df_idx, df_row in df.drop_duplicates('to').iterrows():

                to = df_row['to']

                w3 = Web3(Web3.HTTPProvider(rpc))
                if w3.eth.getCode(w3.toChecksumAddress(to)).hex() != '0x':
                    df = df.loc[df['to'] != to]

            length = df.shape[0]

            if length != 0:
                df['root'] = root
                df['chain'] = chain
                df['tokenName'] = tokenName
                df['tokenSymbol'] = tokenSymbol
                df['token_type'] = token_type

                df.to_csv(f'{WD}/connected_wallet/csv/{root}_{chain}_{token_type}.csv', index=False)

            print(f'{root} find {length} connected wallets. {done}/{total}')


            dfs.loc[(dfs['root'] == root)&(dfs['chain'] == chain), token_type] = length
            dfs.to_csv(f'{WD}/connected_wallet/list/root_list.csv', index=False)
            
    except Exception as e:
        print(f'{root},{chain},error: {e}')
        

### From

In [3]:
dfs = pd.read_csv(f'{WD}/connected_wallet/list_from/root_list.csv')

done = dfs.loc[(dfs['normal_token'] != -1)&(dfs['nft_token'] != -1)].shape[0]
total = dfs.shape[0]
    
for idx, row in dfs.loc[(dfs['normal_token'] == -1)|(dfs['nft_token'] == -1)].iterrows():
    done += 1
    root = row['root']
    chain = row['chain']
    tokenName = row['tokenName']
    tokenSymbol = row['tokenSymbol']
    
    lst = pd.read_csv(f'{RD}connected_accounts/10000filter/root_{chain}_list.csv')
    
    try:
        
        for token_type in ['normal_token', 'nft_token']:
            if lst.loc[lst['root'] == root, token_type].values[0] == 0: 
                dfs.loc[(dfs['root'] == root)&(dfs['chain'] == chain), token_type] = 0
                dfs.to_csv(f'{WD}/connected_wallet/list_from/root_list.csv', index=False)
                print(f'{tokenSymbol} no {token_type}')
                continue
            
            if lst.loc[lst['root'] == root, token_type].values[0] >= 10000:
                print(f'{tokenSymbol} {token_type} more than 10000')
                continue

            df = pd.read_csv(f'{RD}connected_accounts/csv/{root}_{chain}_{token_type}.csv')
            # Transfer out of the Address
            df = df.loc[df['to'] == root]

            # Home Token
            df = df.loc[(df['tokenName'] == tokenName)&(df['tokenSymbol'] == tokenSymbol)]

            # Not Team Finance
            if chain == 'ethereum': 
                df = df.loc[df['from'] != '0xe2fe530c047f2d85298b07d9333c05737f1435fb']
                rpc = 'https://rpc.ankr.com/eth'

            if chain == 'binance': 
                df = df.loc[df['from'] != '0x0c89c0407775dd89b12918b9c0aa42bf96518820']
                rpc = 'https://bscrpc.com'

            if chain == 'avalanche': 
                df = df.loc[df['from'] != '0xe2fe530c047f2d85298b07d9333c05737f1435fb']
                rpc = 'https://api.avax.network/ext/bc/C/rpc'

            if chain == 'fantom': 
                df = df.loc[df['from'] != '0x9f726019452d65a120e1f7ae6b937ee9ebd72440']
                rpc = 'https://rpc.ftm.tools'

            if chain == 'polygon': 
                df = df.loc[df['from'] != '0x3ef7442df454ba6b7c1deec8ddf29cfb2d6e56c7']
                rpc = 'https://polygon-rpc.com'   

            # Not Burn Address
            df = df.loc[(df['from']!= '0x0000000000000000000000000000000000000000')&
                        (df['from']!= '0x000000000000000000000000000000000000dead')
                       ]

            # Not Contract
            for df_idx, df_row in df.drop_duplicates('from').iterrows():

                to = df_row['from']

                w3 = Web3(Web3.HTTPProvider(rpc))
                if w3.eth.getCode(w3.toChecksumAddress(to)).hex() != '0x':
                    df = df.loc[df['from'] != to]

            length = df.shape[0]

            if length != 0:
                df['root'] = root
                df['chain'] = chain
                df['tokenName'] = tokenName
                df['tokenSymbol'] = tokenSymbol
                df['token_type'] = token_type

                df.to_csv(f'{WD}/connected_wallet/csv_from/{root}_{chain}_{token_type}.csv', index=False)

            print(f'{root} find {length} connected wallets. {done}/{total}')


            dfs.loc[(dfs['root'] == root)&(dfs['chain'] == chain), token_type] = length
            dfs.to_csv(f'{WD}/connected_wallet/list_from/root_list.csv', index=False)
            
    except Exception as e:
        print(f'{root},{chain},error: {e}')

FLOKI normal_token more than 10000
0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b find 0 connected wallets. 14706/14807
SKINU normal_token more than 10000
0x165cd37b4c644c2921454429e7f9358d18a45e14 find 0 connected wallets. 14707/14807
BFI normal_token more than 10000
0x2d407ddb06311396fe14d4b49da5f0471447d45c find 0 connected wallets. 14708/14807
CLEANER normal_token more than 10000
0x87fadf44bc06a8c9ae965edfe72ee703cef703c5 find 0 connected wallets. 14709/14807
ROO normal_token more than 10000
ROO no nft_token
SAITAMA normal_token more than 10000
0xae5f8d8b97867dbb1f278127706e1095811d5bf5 find 0 connected wallets. 14711/14807
DSBOWL normal_token more than 10000
0x0107536c8078e071ca90e17200dfec6e58429d01 find 0 connected wallets. 14712/14807
ME normal_token more than 10000
ME no nft_token
NFTASCII normal_token more than 10000
NFTASCII no nft_token
AGSPAD normal_token more than 10000
AGSPAD no nft_token
0xcb10ce4a3d89f76b14e3b30686fa004ef25bc0cb find 5 connected wallets. 14716/14807
DYT nf

## Test

In [2]:
dfs = pd.read_csv(f'{WD}/connected_wallet/list_from/root_list.csv')
dfs.loc[((dfs['normal_token'] == -1) | (dfs['nft_token'] == -1))]

root      tokenName tokenSymbol  \
272    0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b          FLOKI       FLOKI   
569    0x165cd37b4c644c2921454429e7f9358d18a45e14   Zelensky Inu       SKINU   
673    0x2d407ddb06311396fe14d4b49da5f0471447d45c  Bearn Finance         BFI   
704    0x87fadf44bc06a8c9ae965edfe72ee703cef703c5   Shit Cleaner     CLEANER   
705    0xbe7c3dc615245d3404858386ce6e2443ddd4bc25      Lucky Roo         ROO   
...                                           ...            ...         ...   
14118  0xc0c88faf5f7b1045a75f6a88c5b98a47038098f8      Node Game         GME   
14204  0x808996b4af65c316a027a9ada0d395afc27c7385         Ascend        ASND   
14768  0xb2e1ecdc4dddfa1577fa4e0b36d84e4c50d7eb93      CrimeGold       CRIME   
14777  0x5a60d8272781041085d6b48a0901e7ac8838fe37         Pebble         PBL   
14791  0x129f027a491d96abced68cc30976797a42987303  Pleasure Coin        NSFW   

                                  contractAddress      chain  normal_token  \
272    0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   ethereum            -1   
569    0xd9d9869b2c7b1eec43e632a72678085870c288c6   ethereum            -1   
673    0x2840a9fc9ad15738c762e404300761ec828affcb   ethereum            -1   
704    0xe047777381b912eefe3d0549887c34436558d665   ethereum            -1   
705    0x23a6c16b7d533245f3aacff4c22cafc2505acf59   ethereum            -1   
...                                           ...        ...           ...   
14118  0x09F18f55900c9aA168D79a0962E8da71Dab3C319  avalanche            -1   
14204  0xFd0c58F03c83d6960BB9dbFd45076d78Df2F095D  avalanche            -1   
14768  0xF378f05a51868C29D94f57E4240d7423cB526083     fantom            -1   
14777  0x9a2d0935E6CC558aaBa4EbD280F03A74b4752ADd     fantom            -1   
14791  0x8f006d1e1d9dc6c98996f50a4c810f17a47fbf19    polygon            -1   

       nft_token  
272            0  
569            0  
673            0  
704            0  
705            0  
...          ...  
14118          0  
14204         -1  
14768          0  
14777          0  
14791          0  

[102 rows x 7 columns]

In [50]:
dfs.loc[dfs['chain'] == 'polygon'].sample(1)

root              tokenName  \
14778  0x9b09783e11ce3b5abc4cd180cc0ca6ff366a0893  TrustSwap Token (PoS)   

      tokenSymbol                             contractAddress    chain  \
14778        SWAP  0x3809dcdd5dde24b37abe64a5a339784c3323c44f  polygon   

       normal_token  nft_token  
14778             0          0

In [4]:
root = '0xbecca544da77c293e1017a621da5f44374500317'
chain = 'ethereum'
token_type = 'normal_token'
tokenName = 'Citizens of Bulliever Island'
tokenSymbol = 'BULL'

lst = pd.read_csv(f'{RD}connected_accounts/list/root_{chain}_list.csv')
lst.loc[lst['root'] == root, token_type].values[0]

df = pd.read_csv(f'{RD}connected_accounts/csv/{root}_{chain}_{token_type}.csv')
# Transfer out of the Address
df = df.loc[df['from'] == root]

# Home Token
df = df.loc[(df['tokenName'] == tokenName)&(df['tokenSymbol'] == tokenSymbol)]

# Not Team Finance
if chain == 'ethereum': 
    df = df.loc[df['to'] != '0xe2fe530c047f2d85298b07d9333c05737f1435fb']
    rpc = 'https://rpc.ankr.com/eth'
    
if chain == 'binance': 
    df = df.loc[df['to'] != '0x0c89c0407775dd89b12918b9c0aa42bf96518820']
    rpc = 'https://bscrpc.com'
    
if chain == 'avalanche': 
    df = df.loc[df['to'] != '0xe2fe530c047f2d85298b07d9333c05737f1435fb']
    rpc = 'https://api.avax.network/ext/bc/C/rpc'

if chain == 'fantom': 
    df = df.loc[df['to'] != '0x9f726019452d65a120e1f7ae6b937ee9ebd72440']
    rpc = 'https://rpc.ftm.tools'

if chain == 'polygon': 
    df = df.loc[df['to'] != '0x3ef7442df454ba6b7c1deec8ddf29cfb2d6e56c7']
    rpc = 'https://polygon-rpc.com'   

# Not Burn Address
df = df.loc[(df['to']!= '0x0000000000000000000000000000000000000000')&
            (df['to']!= '0x000000000000000000000000000000000000dead')
           ]
df
# Not Contract
for df_idx, df_row in df.drop_duplicates('to').iterrows():
    
    to = df_row['to']
    
    w3 = Web3(Web3.HTTPProvider(rpc))
    if w3.eth.getCode(w3.toChecksumAddress(to)).hex() != '0x':
        df = df.loc[df['to'] != to]
        print(f'{transaction} has contract.')
    else:
        print(f'{transaction} has no contract.')

df

## Debug

In [74]:
root = '0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b'
chain = 'ethereum'
token_type = 'normal_token'
df = pd.read_csv(f'{RD}connected_accounts/csv/{root}_{chain}_{token_type}.csv')
df

In [62]:
lst.loc[lst['root'] == root]

Empty DataFrame
Columns: [Unnamed: 0, root, normal_token, nft_token]
Index: []

In [63]:
dfs.loc[(dfs['normal_token'] == -1)|(dfs['nft_token'] == -1)]

root      tokenName tokenSymbol  \
272    0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b          FLOKI       FLOKI   
569    0x165cd37b4c644c2921454429e7f9358d18a45e14   Zelensky Inu       SKINU   
673    0x2d407ddb06311396fe14d4b49da5f0471447d45c  Bearn Finance         BFI   
704    0x87fadf44bc06a8c9ae965edfe72ee703cef703c5   Shit Cleaner     CLEANER   
705    0xbe7c3dc615245d3404858386ce6e2443ddd4bc25      Lucky Roo         ROO   
...                                           ...            ...         ...   
13913  0x1b8d0e5095bf368a962df1222282720fa33c60de         WIZARD      WIZARD   
14204  0x808996b4af65c316a027a9ada0d395afc27c7385         Ascend        ASND   
14768  0xb2e1ecdc4dddfa1577fa4e0b36d84e4c50d7eb93      CrimeGold       CRIME   
14777  0x5a60d8272781041085d6b48a0901e7ac8838fe37         Pebble         PBL   
14791  0x129f027a491d96abced68cc30976797a42987303  Pleasure Coin        NSFW   

                                  contractAddress      chain  normal_token  \
272    0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   ethereum            -1   
569    0xd9d9869b2c7b1eec43e632a72678085870c288c6   ethereum            -1   
673    0x2840a9fc9ad15738c762e404300761ec828affcb   ethereum            -1   
704    0xe047777381b912eefe3d0549887c34436558d665   ethereum            -1   
705    0x23a6c16b7d533245f3aacff4c22cafc2505acf59   ethereum            -1   
...                                           ...        ...           ...   
13913  0x5066C68cAe3B9BdaCD6A1A37c90F2d1723559D18    binance            -1   
14204  0xFd0c58F03c83d6960BB9dbFd45076d78Df2F095D  avalanche            -1   
14768  0xF378f05a51868C29D94f57E4240d7423cB526083     fantom            -1   
14777  0x9a2d0935E6CC558aaBa4EbD280F03A74b4752ADd     fantom            -1   
14791  0x8f006d1e1d9dc6c98996f50a4c810f17a47fbf19    polygon            -1   

       nft_token  
272           -1  
569           -1  
673           -1  
704           -1  
705           -1  
...          ...  
13913         -1  
14204         -1  
14768         -1  
14777         -1  
14791         -1  

[102 rows x 7 columns]

# Layer One Account (Exclude Self Transfer)

## To

In [133]:
df_to = []
token_type = 'normal_token'
dfs = pd.read_csv(f'{WD}/connected_wallet/list/root_list.csv')

for idx, row in dfs.loc[(dfs['normal_token'] != -1)].iterrows():
    root = row['root']
    chain = row['chain']
    contractAddress = row['contractAddress']
    
    if dfs.loc[(dfs['root'] == root)&(dfs['chain'] == chain), token_type].values[0] == 0: continue
    
    df = pd.read_csv(f'{WD}connected_wallet/csv/{root}_{chain}_{token_type}.csv')
    df = df.loc[df['contractAddress'] == contractAddress]
    df['layer_one'] = df['to']
    df['insider_contractAddress'] = contractAddress
    
    df_to.append(df)
            
df_to = pd.concat(df_to)
df_to

blockNumber   timeStamp  \
0      12935845  1627769329   
0      12959926  1628097268   
1      12960011  1628098587   
2      12965826  1628178359   
3      12966784  1628191014   
..          ...         ...   
52     31333302  1659225869   
53     31438263  1659455165   
54     31509312  1659613562   
55     31525843  1659651119   
56     31525868  1659651169   

                                                                  hash  nonce  \
0   0xdf0dd5cc4dceaccd2af9ac944b686a7726de18c110a60d50aa354017231f28de      4   
0   0x694fe1d0d2d8ff19bca55b0e53555e2d14fcfa1cedf08ee705c096ce626b48da      3   
1   0x65b2dcf9070188e6bd7344064813eb4e0a8fd806012fc3d62f4f501e21689b81      4   
2   0xec8300c162aaa5ed0cda0e067fdf1506baab9975047b5f10f319efd5c9e5c91f      5   
3   0xd3c4e2fd707b91f55ad3b8334960f2019c3a0cc157e5203e8f28dc1e51587160      9   
..                                                                 ...    ...   
52  0x4be302b0e5b42d02724dcfc91bef8480550a67fe6fd4f4f0e67da64529853151     56   
53  0x2c998a0a9cdd4e4ce01287b9b33058aba83035224e0fd2b29a6f72e850940888     57   
54  0xdc4b24b9777b5918c493696a27665ee2917f7258541d3990f5308c14c27938d5     58   
55  0x0647b3df23cd2edc8b099dd93deda0be2b487ac2bf3a7f8e2f899afa89f885e9     59   
56  0x08877e23a646fecc2af15f74a20dc56604e1e5f1fc7d1f8189900e049708ea3a     60   

                                                             blockHash  \
0   0x0f0bf5dd902ff9f7c67c15dd9186c5da38e18f587082aaf2d00a45a8349df5d0   
0   0xf63714944c801e575e6effa0d150bac97544aeedbdc5c4b953ff1df786d449bc   
1   0x67cc1dd6da0b2fadb096387e896a162782263354c36cd4d054e90527d5f2eb59   
2   0xe8e53e64cb5171c29ad6899e80b4bd9203fb803ca96bf5fc6ddbab551a1642cf   
3   0x39e9bb1486085b4549f23b4dfb6dda344dff935d586b0b0ed20e84d3fdb08e12   
..                                                                 ...   
52  0x0410fb1dbab73461792840861722b80b245699f4e1091886ddbce1a2f55f0b85   
53  0xbaf3c52e965491bdd0620c4c3ff43f7b5598de0570e2f5018ea22ef4f7ea947e   
54  0xedd287e7823feebee0398291617d79d5336aedb04ed39e350206c2476dbb9990   
55  0x3df501f5e5ceea307c6e3a85e155f5b3f7a668458f67f587310e28bbf85bb807   
56  0x1a4138b2a0784a1ae5a28f51bb773de8718567a3912256713479244e614969d0   

                                          from  \
0   0x154922e74d108b1f92d702529b31027de54a1933   
0   0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   
1   0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   
2   0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   
3   0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   
..                                         ...   
52  0x61b17f09b2f90e5726b33fb74ae353a8ac04b297   
53  0x61b17f09b2f90e5726b33fb74ae353a8ac04b297   
54  0x61b17f09b2f90e5726b33fb74ae353a8ac04b297   
55  0x61b17f09b2f90e5726b33fb74ae353a8ac04b297   
56  0x61b17f09b2f90e5726b33fb74ae353a8ac04b297   

                               contractAddress  \
0   0xb30fdcc074ef57e43caa44c1a8008e2f9cde647b   
0   0xc065a04ed30471a0200da2e583bac120b129f0c5   
1   0xc065a04ed30471a0200da2e583bac120b129f0c5   
2   0xc065a04ed30471a0200da2e583bac120b129f0c5   
3   0xc065a04ed30471a0200da2e583bac120b129f0c5   
..                                         ...   
52  0xfb32513135e3267995268e3099d2b6114d20b6ed   
53  0xfb32513135e3267995268e3099d2b6114d20b6ed   
54  0xfb32513135e3267995268e3099d2b6114d20b6ed   
55  0xfb32513135e3267995268e3099d2b6114d20b6ed   
56  0xfb32513135e3267995268e3099d2b6114d20b6ed   

                                            to                          value  \
0   0x45f31ccbd796020988f30f33577b8a18a8a20d0f  12500000000000000000000000000   
0   0x566e5faca54503ff0348e75b7321426e7b08f51b       850000000000000000000000   
1   0xfecf93c8c9f261f0a5a82deb7194816ded2ccc4d     20000000000000000000000000   
2   0x533e3c0e6b48010873b947bddc4721b1bdff9648          100000000000000000000   
3   0x4cf2d2086d1c5ba2aca459d63bb363b55284e36a        50000000000000000000000   
..                                         ...                            ...   


In [135]:
df_to = df_to.loc[df_to['from']!= df_to['to']]
df_to.shape[0]

192615

## From

In [136]:
df_from = []
token_type = 'normal_token'
dfs = pd.read_csv(f'{WD}/connected_wallet/list_from/root_list.csv')

for idx, row in dfs.loc[(dfs['normal_token'] != -1)].iterrows():
    root = row['root']
    chain = row['chain']
    contractAddress = row['contractAddress']
    
    if dfs.loc[(dfs['root'] == root)&(dfs['chain'] == chain), token_type].values[0] == 0: continue
    
    df = pd.read_csv(f'{WD}connected_wallet/csv_from/{root}_{chain}_{token_type}.csv')
    df = df.loc[df['contractAddress'] == contractAddress]
    df['layer_one'] = df['from']
    df['insider_contractAddress'] = contractAddress
    
    df_from.append(df)
            
df_from = pd.concat(df_from)
df_from

blockNumber   timeStamp  \
0      12964971  1628166527   
1      12965505  1628173893   
0      12969372  1628225707   
0      12979162  1628355292   
0      11480984  1608345080   
..          ...         ...   
3      31263864  1659072102   
4      31263864  1659072102   
5      31307169  1659168946   
6      31560398  1659730063   
0      24434287  1643747338   

                                                                  hash  \
0   0x77192a6f9aef1986af876ee4ef7107f5130e42e809afa0d15a2ba9283270df29   
1   0xec089b832cfd28e08ad8b372dd6eb9b40cb54fe8c35c1508db6ae9ba9a32bbfe   
0   0x446a9967e93748d7012db5c36215ab4ce01f5890c2c073f600a0d556d4847c50   
0   0x4fbab46271ce0c52a8c0b6cde0b2d2b5205169a080bdaab95a5d56c97b753132   
0   0x42f09563f8775c89444d02566a8795e577b87b54191e6c8ea4c88e4fef14b123   
..                                                                 ...   
3   0x91aa264f438c8cc438f9aacbc37f69ed6341c732af9d1b157d35f46a3261350e   
4   0xc92432598cc2690d270ec874a1787f6dda22336cf850ef6c8fead5e7e210db4f   
5   0x808fcbe17fbad5d6e1a9647ccbadaadce8443f333cd775922c9375ca4eab37f9   
6   0x9cf796b5c050a1d5ff8ac8259ebe8795f55bd474168d932bed0717482da4816e   
0   0x448605b66a8539f789bcb6333486d0da229a8347b6c06bba41ef0e5c4d022900   

      nonce  \
0         0   
1         2   
0         0   
0         1   
0   5967538   
..      ...   
3      1575   
4      1576   
5         0   
6         0   
0        22   

                                                             blockHash  \
0   0x20f4fa8d166ece1d2f229927ad024144040259cca06f956abc89b6469cf05640   
1   0x79980eb1360374f639e0563fcc729e03877f7e867bf9d3f0b79f0b609a06c4bd   
0   0x3a35068af2a60203d2bc5dbf93c8025f5ee2e508bd87579212a3284fe4bc0b31   
0   0xc0484f8dc1d553542023a32fbb51ecf2d4f501d501d196847acc1baca3ee8734   
0   0xee678ec4abbfceae9aa09e2ea7193e474e72f9f102538a1ea2f36fac720f8698   
..                                                                 ...   
3   0x882e906c092801de8b53c3aac6e6b34d855b86294a9b83d06b88d9a434ebd533   
4   0x882e906c092801de8b53c3aac6e6b34d855b86294a9b83d06b88d9a434ebd533   
5   0xb04d427d39a03c7fbd844aaca454b696ec3490243777e8d6fa51604f6ac7a85e   
6   0xe5a4d8b3de84361be50970821c3d48e79d8e759e803d43ab102b5bbddce123e4   
0   0x30f7f0e5256e7b8c7ef7769f49fcd08b4a6ece6e68e3e9a2b617c8d35cafdefa   

                                          from  \
0   0x6821a3ede3ec34fcf603c5c0daf8504dafb97420   
1   0x6821a3ede3ec34fcf603c5c0daf8504dafb97420   
0   0x60c279c61b86bf58cd4d26b06d277bd6993bb4f5   
0   0xfecf93c8c9f261f0a5a82deb7194816ded2ccc4d   
0   0x3f5ce5fbfe3e9af3971dd833d26ba9b5c936f0be   
..                                         ...   
3   0xe0a616c3659be29567e08819772e6905307adf21   
4   0xe0a616c3659be29567e08819772e6905307adf21   
5   0xc2e80a0ce4ddbef14e83a2cfdeb8d7e45c28e699   
6   0x2631945cf0912d09acaf9b9172878c5fac7816b7   
0   0x885f5fd87e62ed2ebd0b0bb1c295c4c43edee5b5   

                               contractAddress  \
0   0x0239d3a3485ec54511bee9d77d92695e443bf060   
1   0x0239d3a3485ec54511bee9d77d92695e443bf060   
0   0x18084be33d80c3fdf6e7e7deab4a4e5e26657331   
0   0xc065a04ed30471a0200da2e583bac120b129f0c5   
0   0x1f9840a85d5af5bf1d1762f925bdaddc4201f984   
..                                         ...   
3   0xfb32513135e3267995268e3099d2b6114d20b6ed   
4   0xfb32513135e3267995268e3099d2b6114d20b6ed   
5   0xfb32513135e3267995268e3099d2b6114d20b6ed   
6   0xfb32513135e3267995268e3099d2b6114d20b6ed   
0   0x21f9b5b2626603e3f40bfc13d01afb8c431d382f   

                                            to                        value  \
0   0xa2608089b0c7321f10c1a28f9952d59781dab59b          1000000000000000000   
1   0xa2608089b0c7321f10c1a28f9952d59781dab59b  159999999000000000000000000   
0   0x24e8f3941916781a1e934426fb9d331ad2a01a5c                1070000000000   
0   0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   20000000000000000000000000   
0   0x51a1318fc8c8822e7461a3054599b5f5efe94d5f        506251849990000000000

In [137]:
df_from = df_from.loc[df_from['from']!= df_from['to']]
df_from.shape[0]

55301

## Panel (Exclude Zero)

### Exclude Zero

In [224]:
panel = []
panel.append(df_to)
panel.append(df_from)
panel = pd.concat(panel)

panel['avg_priceUSD'] = 0
panel['token_number'] = panel['value'].astype('float') / 10**panel['tokenDecimal']
panel['status'] = -1
panel

blockNumber   timeStamp  \
0      12935845  1627769329   
0      12959926  1628097268   
1      12960011  1628098587   
2      12965826  1628178359   
3      12966784  1628191014   
..          ...         ...   
3      31263864  1659072102   
4      31263864  1659072102   
5      31307169  1659168946   
6      31560398  1659730063   
0      24434287  1643747338   

                                                                  hash  nonce  \
0   0xdf0dd5cc4dceaccd2af9ac944b686a7726de18c110a60d50aa354017231f28de      4   
0   0x694fe1d0d2d8ff19bca55b0e53555e2d14fcfa1cedf08ee705c096ce626b48da      3   
1   0x65b2dcf9070188e6bd7344064813eb4e0a8fd806012fc3d62f4f501e21689b81      4   
2   0xec8300c162aaa5ed0cda0e067fdf1506baab9975047b5f10f319efd5c9e5c91f      5   
3   0xd3c4e2fd707b91f55ad3b8334960f2019c3a0cc157e5203e8f28dc1e51587160      9   
..                                                                 ...    ...   
3   0x91aa264f438c8cc438f9aacbc37f69ed6341c732af9d1b157d35f46a3261350e   1575   
4   0xc92432598cc2690d270ec874a1787f6dda22336cf850ef6c8fead5e7e210db4f   1576   
5   0x808fcbe17fbad5d6e1a9647ccbadaadce8443f333cd775922c9375ca4eab37f9      0   
6   0x9cf796b5c050a1d5ff8ac8259ebe8795f55bd474168d932bed0717482da4816e      0   
0   0x448605b66a8539f789bcb6333486d0da229a8347b6c06bba41ef0e5c4d022900     22   

                                                             blockHash  \
0   0x0f0bf5dd902ff9f7c67c15dd9186c5da38e18f587082aaf2d00a45a8349df5d0   
0   0xf63714944c801e575e6effa0d150bac97544aeedbdc5c4b953ff1df786d449bc   
1   0x67cc1dd6da0b2fadb096387e896a162782263354c36cd4d054e90527d5f2eb59   
2   0xe8e53e64cb5171c29ad6899e80b4bd9203fb803ca96bf5fc6ddbab551a1642cf   
3   0x39e9bb1486085b4549f23b4dfb6dda344dff935d586b0b0ed20e84d3fdb08e12   
..                                                                 ...   
3   0x882e906c092801de8b53c3aac6e6b34d855b86294a9b83d06b88d9a434ebd533   
4   0x882e906c092801de8b53c3aac6e6b34d855b86294a9b83d06b88d9a434ebd533   
5   0xb04d427d39a03c7fbd844aaca454b696ec3490243777e8d6fa51604f6ac7a85e   
6   0xe5a4d8b3de84361be50970821c3d48e79d8e759e803d43ab102b5bbddce123e4   
0   0x30f7f0e5256e7b8c7ef7769f49fcd08b4a6ece6e68e3e9a2b617c8d35cafdefa   

                                          from  \
0   0x154922e74d108b1f92d702529b31027de54a1933   
0   0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   
1   0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   
2   0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   
3   0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   
..                                         ...   
3   0xe0a616c3659be29567e08819772e6905307adf21   
4   0xe0a616c3659be29567e08819772e6905307adf21   
5   0xc2e80a0ce4ddbef14e83a2cfdeb8d7e45c28e699   
6   0x2631945cf0912d09acaf9b9172878c5fac7816b7   
0   0x885f5fd87e62ed2ebd0b0bb1c295c4c43edee5b5   

                               contractAddress  \
0   0xb30fdcc074ef57e43caa44c1a8008e2f9cde647b   
0   0xc065a04ed30471a0200da2e583bac120b129f0c5   
1   0xc065a04ed30471a0200da2e583bac120b129f0c5   
2   0xc065a04ed30471a0200da2e583bac120b129f0c5   
3   0xc065a04ed30471a0200da2e583bac120b129f0c5   
..                                         ...   
3   0xfb32513135e3267995268e3099d2b6114d20b6ed   
4   0xfb32513135e3267995268e3099d2b6114d20b6ed   
5   0xfb32513135e3267995268e3099d2b6114d20b6ed   
6   0xfb32513135e3267995268e3099d2b6114d20b6ed   
0   0x21f9b5b2626603e3f40bfc13d01afb8c431d382f   

                                            to                          value  \
0   0x45f31ccbd796020988f30f33577b8a18a8a20d0f  12500000000000000000000000000   
0   0x566e5faca54503ff0348e75b7321426e7b08f51b       850000000000000000000000   
1   0xfecf93c8c9f261f0a5a82deb7194816ded2ccc4d     20000000000000000000000000   
2   0x533e3c0e6b48010873b947bddc4721b1bdff9648          100000000000000000000   
3   0x4cf2d2086d1c5ba2aca459d63bb363b55284e36a        50000000000000000000000   
..                                         ...                            ...   


### Timestamp

In [225]:
panel['datetime'] = pd.to_datetime(panel['timeStamp'], unit='s', origin='unix')
panel['date'] = panel['datetime'].dt.strftime('%Y-%m-%d')
panel

blockNumber   timeStamp  \
0      12935845  1627769329   
0      12959926  1628097268   
1      12960011  1628098587   
2      12965826  1628178359   
3      12966784  1628191014   
..          ...         ...   
3      31263864  1659072102   
4      31263864  1659072102   
5      31307169  1659168946   
6      31560398  1659730063   
0      24434287  1643747338   

                                                                  hash  nonce  \
0   0xdf0dd5cc4dceaccd2af9ac944b686a7726de18c110a60d50aa354017231f28de      4   
0   0x694fe1d0d2d8ff19bca55b0e53555e2d14fcfa1cedf08ee705c096ce626b48da      3   
1   0x65b2dcf9070188e6bd7344064813eb4e0a8fd806012fc3d62f4f501e21689b81      4   
2   0xec8300c162aaa5ed0cda0e067fdf1506baab9975047b5f10f319efd5c9e5c91f      5   
3   0xd3c4e2fd707b91f55ad3b8334960f2019c3a0cc157e5203e8f28dc1e51587160      9   
..                                                                 ...    ...   
3   0x91aa264f438c8cc438f9aacbc37f69ed6341c732af9d1b157d35f46a3261350e   1575   
4   0xc92432598cc2690d270ec874a1787f6dda22336cf850ef6c8fead5e7e210db4f   1576   
5   0x808fcbe17fbad5d6e1a9647ccbadaadce8443f333cd775922c9375ca4eab37f9      0   
6   0x9cf796b5c050a1d5ff8ac8259ebe8795f55bd474168d932bed0717482da4816e      0   
0   0x448605b66a8539f789bcb6333486d0da229a8347b6c06bba41ef0e5c4d022900     22   

                                                             blockHash  \
0   0x0f0bf5dd902ff9f7c67c15dd9186c5da38e18f587082aaf2d00a45a8349df5d0   
0   0xf63714944c801e575e6effa0d150bac97544aeedbdc5c4b953ff1df786d449bc   
1   0x67cc1dd6da0b2fadb096387e896a162782263354c36cd4d054e90527d5f2eb59   
2   0xe8e53e64cb5171c29ad6899e80b4bd9203fb803ca96bf5fc6ddbab551a1642cf   
3   0x39e9bb1486085b4549f23b4dfb6dda344dff935d586b0b0ed20e84d3fdb08e12   
..                                                                 ...   
3   0x882e906c092801de8b53c3aac6e6b34d855b86294a9b83d06b88d9a434ebd533   
4   0x882e906c092801de8b53c3aac6e6b34d855b86294a9b83d06b88d9a434ebd533   
5   0xb04d427d39a03c7fbd844aaca454b696ec3490243777e8d6fa51604f6ac7a85e   
6   0xe5a4d8b3de84361be50970821c3d48e79d8e759e803d43ab102b5bbddce123e4   
0   0x30f7f0e5256e7b8c7ef7769f49fcd08b4a6ece6e68e3e9a2b617c8d35cafdefa   

                                          from  \
0   0x154922e74d108b1f92d702529b31027de54a1933   
0   0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   
1   0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   
2   0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   
3   0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   
..                                         ...   
3   0xe0a616c3659be29567e08819772e6905307adf21   
4   0xe0a616c3659be29567e08819772e6905307adf21   
5   0xc2e80a0ce4ddbef14e83a2cfdeb8d7e45c28e699   
6   0x2631945cf0912d09acaf9b9172878c5fac7816b7   
0   0x885f5fd87e62ed2ebd0b0bb1c295c4c43edee5b5   

                               contractAddress  \
0   0xb30fdcc074ef57e43caa44c1a8008e2f9cde647b   
0   0xc065a04ed30471a0200da2e583bac120b129f0c5   
1   0xc065a04ed30471a0200da2e583bac120b129f0c5   
2   0xc065a04ed30471a0200da2e583bac120b129f0c5   
3   0xc065a04ed30471a0200da2e583bac120b129f0c5   
..                                         ...   
3   0xfb32513135e3267995268e3099d2b6114d20b6ed   
4   0xfb32513135e3267995268e3099d2b6114d20b6ed   
5   0xfb32513135e3267995268e3099d2b6114d20b6ed   
6   0xfb32513135e3267995268e3099d2b6114d20b6ed   
0   0x21f9b5b2626603e3f40bfc13d01afb8c431d382f   

                                            to                          value  \
0   0x45f31ccbd796020988f30f33577b8a18a8a20d0f  12500000000000000000000000000   
0   0x566e5faca54503ff0348e75b7321426e7b08f51b       850000000000000000000000   
1   0xfecf93c8c9f261f0a5a82deb7194816ded2ccc4d     20000000000000000000000000   
2   0x533e3c0e6b48010873b947bddc4721b1bdff9648          100000000000000000000   
3   0x4cf2d2086d1c5ba2aca459d63bb363b55284e36a        50000000000000000000000   
..                                         ...                            ...   


### Duplicated

In [237]:
panel.drop_duplicates(['insider_contractAddress', 'timeStamp']).shape[0]
panel.drop_duplicates(['insider_contractAddress', 'date']).shape[0]
panel.loc[panel['chain'] == 'ethereum'].sample(1)

120806

12535

blockNumber   timeStamp  \
6569     14280150  1645857865   

                                                                    hash  \
6569  0xa5881b2b78c42f795a94f8fe859becd274045dc885cc8f9759373d7d6b55313c   

      nonce  \
6569     18   

                                                               blockHash  \
6569  0x9f19d77e6abed0f53f7041e0e25d7be6cbcb3fe1ae5d792129ac4f98f018d37c   

                                            from  \
6569  0xbecca544da77c293e1017a621da5f44374500317   

                                 contractAddress  \
6569  0x5824e2d508da5055c12046b0155cfd83d4b106f9   

                                              to                   value  \
6569  0xd1bd5ae400123d21d44df95a93136a9409d133c9  1991046296296292154920   

                         tokenName tokenSymbol  tokenDecimal  \
6569  Citizens of Bulliever Island        BULL          18.0   

      transactionIndex      gas     gasPrice  gasUsed  cumulativeGasUsed  \
6569                78  1445848  35044527932  1305904            6203795   

           input  confirmations                                        root  \
6569  deprecated         989875  0xbecca544da77c293e1017a621da5f44374500317   

         chain    token_type                                   layer_one  \
6569  ethereum  normal_token  0xd1bd5ae400123d21d44df95a93136a9409d133c9   

                         insider_contractAddress  avg_priceUSD  token_number  \
6569  0x5824e2d508da5055c12046b0155cfd83d4b106f9             0   1991.046296   

      status            datetime        date  
6569      -1 2022-02-26 06:44:25  2022-02-26

In [227]:
panel.to_csv(f'{WD}connected_wallet/panel/panel.csv', index=False)

# Layer One Account (Exclude Penny Transaction)

In [228]:
import datetime
df = pd.read_csv(f'{WD}connected_wallet/panel/panel.csv')

dexes = {'ethereum':['uniswapv3_ethereum', 'uniswapv2_ethereum', 'sushiswap_ethereum'],
     'binance':['pancake_binance', 'biswap_binance', 'apeswap_binance', 'babyswap_binance', 'jetswap_binance'],
     'avalanche':['traderjoe_avalanche', 'pangolin_avalanche'],
     'fantom':['spookyswap_fantom', 'spiritswap_fantom'],
     'polygon':['sushiswap_polygon', 'apeswap_polygon', 'jetswap_polygon']}

done = df.loc[df['status'] != -1].drop_duplicates(['insider_contractAddress', 'date']).shape[0]
total = df.drop_duplicates(['insider_contractAddress', 'date']).shape[0]
starttime = datetime.datetime.now()

for idx, row in df.loc[df['status'] == -1].drop_duplicates(['insider_contractAddress', 'date']).iterrows():
    try:

        done += 1
        
        endtime = datetime.datetime.now()
        duration = (endtime-starttime).seconds / 60
        lefttime = (duration / (done + 1)) * (total- done)
        print(f'{done}/{total}, {lefttime} min left')
        
        contract = row['insider_contractAddress']
        contractAddress_lower = contract.lower()
        contractAddress_upper = Web3.toChecksumAddress(contractAddress_lower)

        root = row['root']
        chain = row['chain']
        date = row['date']
        timestamp = pd.to_datetime(row['timeStamp'], unit='s', origin='unix')

        priceUSD = 0
        dex_num = 0
        avg_priceUSD = 0

        for dex in dexes[chain]:
            lst = pd.read_csv(f'{WD}/dex_price/list_all/{dex}.csv')
            csv_info = lst.loc[((lst['contractAddress'] == contractAddress_lower)|
                                (lst['contractAddress'] == contractAddress_upper))&
                               (lst['root'] == root)
                              ]
            if csv_info['contractAddress'].values[0] == contractAddress_lower:
                contractAddress = contractAddress_lower
            else:
                contractAddress = contractAddress_upper

            status = csv_info['status'].values[0]
            dexn = csv_info['dex'].values[0]

            if status == 0: 
                continue
            elif dexn == 0:
                continue
            else:
                csv = pd.read_csv(f'{WD}dex_price/csv_all/{contractAddress}_{dex}.csv') 
                price_info = csv.loc[(pd.to_datetime(csv['date']) > pd.to_datetime(timestamp) - datetime.timedelta(days=1))&
                                  (pd.to_datetime(csv['date']) < pd.to_datetime(timestamp))]
                
                if price_info.shape[0] != 0:
                    price = price_info['priceUSD'].values[0]
                    if price != 0:  
                        priceUSD += price
                        dex_num += 1

        if dex_num != 0: 
            df.loc[(df['insider_contractAddress'] == contract)&(df['date'] == date), 'avg_priceUSD'] = priceUSD/dex_num
            print(f'average price: {priceUSD/dex_num}')
        
        df.loc[(df['insider_contractAddress'] == contract)&(df['date'] == date), 'status'] = 1

    except Exception as e:
        print(f'Error:{e}')
        
df.to_csv(f'{WD}connected_wallet/panel/panel.csv', index=False)

1/12535, 0.0 min left
2/12535, 0.0 min left
3/12535, 0.0 min left
4/12535, 0.0 min left
5/12535, 0.0 min left
6/12535, 0.0 min left
7/12535, 0.0 min left
8/12535, 0.0 min left
9/12535, 20.876666666666665 min left
10/12535, 18.977272727272727 min left
11/12535, 17.394444444444446 min left
12/12535, 16.055128205128206 min left
13/12535, 14.907142857142857 min left
14/12535, 13.912222222222223 min left
15/12535, 13.041666666666666 min left
average price: 1777.3700524470885
16/12535, 12.273529411764706 min left
17/12535, 23.181481481481484 min left
18/12535, 21.95964912280702 min left
19/12535, 20.86 min left
20/12535, 19.865079365079364 min left
21/12535, 18.96060606060606 min left
22/12535, 18.13478260869565 min left
23/12535, 17.37777777777778 min left
average price: 8.614074480827647
24/12535, 16.68133333333333 min left
average price: 21.25361036011255
25/12535, 24.05769230769231 min left
average price: 23.18317108718068
26/12535, 23.164814814814815 min left
average price: 26.189405278

## Excldue Penny Transaction

In [308]:
df = pd.read_csv(f'{WD}connected_wallet/panel/panel.csv')
df['amountUSD'] = df['avg_priceUSD'] * df['token_number']
df

blockNumber   timeStamp  \
0          12935845  1627769329   
1          12959926  1628097268   
2          12960011  1628098587   
3          12965826  1628178359   
4          12966784  1628191014   
...             ...         ...   
247911     31263864  1659072102   
247912     31263864  1659072102   
247913     31307169  1659168946   
247914     31560398  1659730063   
247915     24434287  1643747338   

                                                                      hash  \
0       0xdf0dd5cc4dceaccd2af9ac944b686a7726de18c110a60d50aa354017231f28de   
1       0x694fe1d0d2d8ff19bca55b0e53555e2d14fcfa1cedf08ee705c096ce626b48da   
2       0x65b2dcf9070188e6bd7344064813eb4e0a8fd806012fc3d62f4f501e21689b81   
3       0xec8300c162aaa5ed0cda0e067fdf1506baab9975047b5f10f319efd5c9e5c91f   
4       0xd3c4e2fd707b91f55ad3b8334960f2019c3a0cc157e5203e8f28dc1e51587160   
...                                                                    ...   
247911  0x91aa264f438c8cc438f9aacbc37f69ed6341c732af9d1b157d35f46a3261350e   
247912  0xc92432598cc2690d270ec874a1787f6dda22336cf850ef6c8fead5e7e210db4f   
247913  0x808fcbe17fbad5d6e1a9647ccbadaadce8443f333cd775922c9375ca4eab37f9   
247914  0x9cf796b5c050a1d5ff8ac8259ebe8795f55bd474168d932bed0717482da4816e   
247915  0x448605b66a8539f789bcb6333486d0da229a8347b6c06bba41ef0e5c4d022900   

        nonce  \
0           4   
1           3   
2           4   
3           5   
4           9   
...       ...   
247911   1575   
247912   1576   
247913      0   
247914      0   
247915     22   

                                                                 blockHash  \
0       0x0f0bf5dd902ff9f7c67c15dd9186c5da38e18f587082aaf2d00a45a8349df5d0   
1       0xf63714944c801e575e6effa0d150bac97544aeedbdc5c4b953ff1df786d449bc   
2       0x67cc1dd6da0b2fadb096387e896a162782263354c36cd4d054e90527d5f2eb59   
3       0xe8e53e64cb5171c29ad6899e80b4bd9203fb803ca96bf5fc6ddbab551a1642cf   
4       0x39e9bb1486085b4549f23b4dfb6dda344dff935d586b0b0ed20e84d3fdb08e12   
...                                                                    ...   
247911  0x882e906c092801de8b53c3aac6e6b34d855b86294a9b83d06b88d9a434ebd533   
247912  0x882e906c092801de8b53c3aac6e6b34d855b86294a9b83d06b88d9a434ebd533   
247913  0xb04d427d39a03c7fbd844aaca454b696ec3490243777e8d6fa51604f6ac7a85e   
247914  0xe5a4d8b3de84361be50970821c3d48e79d8e759e803d43ab102b5bbddce123e4   
247915  0x30f7f0e5256e7b8c7ef7769f49fcd08b4a6ece6e68e3e9a2b617c8d35cafdefa   

                                              from  \
0       0x154922e74d108b1f92d702529b31027de54a1933   
1       0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   
2       0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   
3       0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   
4       0x2d74bee7ffdec1c70218c439475319d81a5cf8ec   
...                                            ...   
247911  0xe0a616c3659be29567e08819772e6905307adf21   
247912  0xe0a616c3659be29567e08819772e6905307adf21   
247913  0xc2e80a0ce4ddbef14e83a2cfdeb8d7e45c28e699   
247914  0x2631945cf0912d09acaf9b9172878c5fac7816b7   
247915  0x885f5fd87e62ed2ebd0b0bb1c295c4c43edee5b5   

                                   contractAddress  \
0       0xb30fdcc074ef57e43caa44c1a8008e2f9cde647b   
1       0xc065a04ed30471a0200da2e583bac120b129f0c5   
2       0xc065a04ed30471a0200da2e583bac120b129f0c5   
3       0xc065a04ed30471a0200da2e583bac120b129f0c5   
4       0xc065a04ed30471a0200da2e583bac120b129f0c5   
...                                            ...   
247911  0xfb32513135e3267995268e3099d2b6114d20b6ed   
247912  0xfb32513135e3267995268e3099d2b6114d20b6ed   
247913  0xfb32513135e3267995268e3099d2b6114d20b6ed   
247914  0xfb32513135e3267995268e3099d2b6114d20b6ed   
247915  0x21f9b5b2626603e3f40bfc13d01afb8c431d382f   

                                                to  \
0       0x45f31ccbd796020988f30f33577b8a18a8a20d0f   
1       0x566e5faca54503ff0348e75b7321426e7b08f51b   
2       0xfecf93c8c9f261f0a5a82deb7194816ded2ccc

In [309]:
df['layer_one'].duplicated().sum()
df[['layer_one', 'insider_contractAddress']].duplicated().sum()
df[['layer_one', 'insider_contractAddress', 'chain']].duplicated().sum()

dff = df.groupby(['layer_one', 'insider_contractAddress', 'chain'])['amountUSD'].sum().reset_index()
dff = dff.loc[dff['amountUSD'] >= 1000]

102664

90736

90735

## Exclude Another Burn Address

In [310]:
dff = dff.loc[dff['layer_one']!= '0x0000000000000000000000000000000000000001']
dff.to_csv(f'{WD}connected_wallet/panel/panel_large_amount.csv', index=False)

## Test

In [246]:
def token_dollar_price(contract, root, chain, timestamp):
    
        contractAddress_lower = contract.lower()
        contractAddress_upper = Web3.toChecksumAddress(contractAddress_lower)

        timestamp = pd.to_datetime(timestamp, unit='s', origin='unix')
        date = timestamp.strftime('%Y-%m-%d')
        
        priceUSD = 0
        dex_num = 0
        avg_priceUSD = 0

        for dex in dexes[chain]:
            lst = pd.read_csv(f'{WD}/dex_price/list_all/{dex}.csv')
            csv_info = lst.loc[((lst['contractAddress'] == contractAddress_lower)|
                                (lst['contractAddress'] == contractAddress_upper))&
                               (lst['root'] == root)
                              ]
            if csv_info['contractAddress'].values[0] == contractAddress_lower:
                contractAddress = contractAddress_lower
            else:
                contractAddress = contractAddress_upper

            status = csv_info['status'].values[0]
            dexn = csv_info['dex'].values[0]

            if status == 0: 
                continue
            elif dexn == 0:
                continue
            else:
                csv = pd.read_csv(f'{WD}dex_price/csv_all/{contractAddress}_{dex}.csv') 
                price_info = csv.loc[(pd.to_datetime(csv['date']) > pd.to_datetime(timestamp) - datetime.timedelta(days=1))&
                                  (pd.to_datetime(csv['date']) < pd.to_datetime(timestamp))]
                
                if price_info.shape[0] != 0:
                    price = price_info['priceUSD'].values[0]
                    if price != 0:  
                        priceUSD += price
                        dex_num += 1

        if dex_num != 0: 
            return priceUSD/dex_num
        if dex_num == 0:
            return 0

## Function

In [247]:
token_dollar_price(contract='0x834806a97938ae7270d3dfef01240206b380e716',
                   root = '0xc77dd9685467194323321f229b9e2fd1692778d0',
                   chain = 'ethereum',
                   timestamp = '1628578128')

1777.3700524470885

In [243]:
contractAddress_lower = '0x834806a97938ae7270d3dfef01240206b380e716'.lower()
contractAddress_upper = Web3.toChecksumAddress(contractAddress_lower)
root = '0xc77dd9685467194323321f229b9e2fd1692778d0'
chain = 'ethereum'
timestamp = pd.to_datetime('1628578128', unit='s', origin='unix')
priceUSD = 0
dex_num = 0
avg_priceUSD = 0

timestamp
for dex in dexes[chain]:
    dex
    lst = pd.read_csv(f'{WD}/dex_price/list_all/{dex}.csv')
    csv_info = lst.loc[((lst['contractAddress'] == contractAddress_lower)|
                        (lst['contractAddress'] == contractAddress_upper))&
                       (lst['root'] == root)
                      ]
    csv_info
    if csv_info['contractAddress'].values[0] == contractAddress_lower:
        contractAddress = contractAddress_lower
    else:
        contractAddress = contractAddress_upper

    status = csv_info['status'].values[0]
    dexn = csv_info['dex'].values[0]

    status, dexn

    if status == 0: 
        pass
    elif dexn == 0:
        pass
    else:
        csv = pd.read_csv(f'{WD}dex_price/csv_all/{contractAddress}_{dex}.csv') 
        price_info = csv.loc[(pd.to_datetime(csv['date']) > pd.to_datetime(timestamp) - datetime.timedelta(days=1))&
                          (pd.to_datetime(csv['date']) < pd.to_datetime(timestamp))]
        
        if price_info.shape[0] != 0:
            price = price_info['priceUSD'].values[0]
            if price != 0:  
                priceUSD += price
                dex_num += 1
            
if dex_num != 0: avg_priceUSD = priceUSD/dex_num  

avg_priceUSD

Timestamp('2021-08-10 06:48:48')

'uniswapv3_ethereum'

root      tokenName tokenSymbol  \
13  0xc77dd9685467194323321f229b9e2fd1692778d0  RunwayDiamond    RNWY????   

                               contractAddress  status  dex  
13  0x834806a97938ae7270d3dfef01240206b380e716       1  0.0

(1, 0.0)

'uniswapv2_ethereum'

...

(1, 1.0)

'sushiswap_ethereum'

root      tokenName tokenSymbol  \
13  0xc77dd9685467194323321f229b9e2fd1692778d0  RunwayDiamond    RNWY????   

                               contractAddress  status  dex  
13  0x834806a97938ae7270d3dfef01240206b380e716       1  0.0

(1, 0.0)

1777.3700524470885

# More than 10,000

In [248]:
dfs = pd.read_csv(f'{WD}/connected_wallet/list/root_list.csv')
dfs

root       tokenName tokenSymbol  \
0      0x742025b32fdda654df1aa5ae348928331ff05062        Callisto       C3000   
1      0xef0121d57d9e4324c3de83cf2a686ff5ac13c3a4        Callisto       C3000   
2      0xa625141e73ab1af1b57efbbad9ba9ab8813393e3            SYNC        SYNC   
3      0x6e86c831b85cc37f0aeeb5d553c40b257af8fb42  t.me/skin_port    SKINPORT   
4      0x72969afa049fa40e808d42f807ef4640a7cac5ec    KING VITALIK   KING ????   
...                                           ...             ...         ...   
14802  0x4dbe648f797e7ec51da3eae23a89b971b4e022a5     Chihiro Inu       CHIRO   
14803  0x5a6dc942826807539ca19d21c132e4b004075de0  NextEarthToken        NXTT   
14804  0x3030f09fe7ea8fa6762c13d12afa8541cb2c6644          Dogioh         DGH   
14805  0x81411b800dcc935e1aaf0ed01dd1c0777236153c            POKI        POKI   
14806  0xadc42c844b8392ca353e079030609b6303d7f51d            Poge        Poge   

                                  contractAddress     chain  normal_token  \
0      0x2a15de7c821baa1a727039b76d540b36b23db257  ethereum             0   
1      0xa0fd12272cc4da86aebf9d592cdad253cbbc25fb  ethereum             0   
2      0xb6ff96b8a8d214544ca0dbc9b33f7ad6503efd32  ethereum             0   
3      0x506d62bf7d8a8f444f13533081dc03470483f4ea  ethereum             0   
4      0xcbfb937a75f8baf9d94e064cc90b1c045f7c25fa  ethereum             0   
...                                           ...       ...           ...   
14802  0x35156b404C3f9bdaf45ab65Ba315419bcDe3775c   polygon             0   
14803  0x0d0B8488222F7f83B23E365320a4021b12eAD608   polygon             0   
14804  0x87842eD511C255a06aE872E7Ad83a64a1e3bD39c   polygon            42   
14805  0x3E41CE4f7ef7ca7C23640d2C8a906552a2A90092   polygon             0   
14806  0x6EA856c7A96d7366De2bbB600B956617d344DDa4   polygon             5   

       nft_token  
0              0  
1              0  
2              0  
3              0  
4              0  
...          ...  
14802          0  
14803          0  
14804          0  
14805          0  
14806          0  

[14807 rows x 7 columns]

## To

In [311]:
dfs = pd.read_csv(f'{WD}/connected_wallet/list/root_list.csv')
dfs.loc[(dfs['normal_token'] == -1)|(dfs['nft_token'] == -1)]

root      tokenName tokenSymbol  \
272    0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b          FLOKI       FLOKI   
569    0x165cd37b4c644c2921454429e7f9358d18a45e14   Zelensky Inu       SKINU   
673    0x2d407ddb06311396fe14d4b49da5f0471447d45c  Bearn Finance         BFI   
704    0x87fadf44bc06a8c9ae965edfe72ee703cef703c5   Shit Cleaner     CLEANER   
705    0xbe7c3dc615245d3404858386ce6e2443ddd4bc25      Lucky Roo         ROO   
...                                           ...            ...         ...   
13913  0x1b8d0e5095bf368a962df1222282720fa33c60de         WIZARD      WIZARD   
14204  0x808996b4af65c316a027a9ada0d395afc27c7385         Ascend        ASND   
14768  0xb2e1ecdc4dddfa1577fa4e0b36d84e4c50d7eb93      CrimeGold       CRIME   
14777  0x5a60d8272781041085d6b48a0901e7ac8838fe37         Pebble         PBL   
14791  0x129f027a491d96abced68cc30976797a42987303  Pleasure Coin        NSFW   

                                  contractAddress      chain  normal_token  \
272    0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   ethereum            -1   
569    0xd9d9869b2c7b1eec43e632a72678085870c288c6   ethereum            -1   
673    0x2840a9fc9ad15738c762e404300761ec828affcb   ethereum            -1   
704    0xe047777381b912eefe3d0549887c34436558d665   ethereum            -1   
705    0x23a6c16b7d533245f3aacff4c22cafc2505acf59   ethereum            -1   
...                                           ...        ...           ...   
13913  0x5066C68cAe3B9BdaCD6A1A37c90F2d1723559D18    binance            -1   
14204  0xFd0c58F03c83d6960BB9dbFd45076d78Df2F095D  avalanche            -1   
14768  0xF378f05a51868C29D94f57E4240d7423cB526083     fantom            -1   
14777  0x9a2d0935E6CC558aaBa4EbD280F03A74b4752ADd     fantom            -1   
14791  0x8f006d1e1d9dc6c98996f50a4c810f17a47fbf19    polygon            -1   

       nft_token  
272           -1  
569           -1  
673           -1  
704           -1  
705           -1  
...          ...  
13913         -1  
14204         -1  
14768         -1  
14777         -1  
14791         -1  

[102 rows x 7 columns]

In [321]:
dfs = pd.read_csv(f'{WD}/connected_wallet/list/root_list.csv')

done = dfs.loc[(dfs['normal_token'] != -1)&(dfs['nft_token'] != -1)].shape[0]
total = dfs.shape[0]
supplement = []
    
for idx, row in dfs.loc[(dfs['normal_token'] == -1)|(dfs['nft_token'] == -1)].iterrows():
    done += 1
    root = row['root']
    chain = row['chain']
    tokenName = row['tokenName']
    tokenSymbol = row['tokenSymbol']
    contractAddress = row['contractAddress']

    lst = pd.read_csv(f'{RD}connected_accounts/list/root_{chain}_list.csv')
    
    try:
        
        for token_type in ['normal_token']:
            if lst.loc[lst['root'] == root, token_type].values[0] == 0: 
                dfs.loc[(dfs['root'] == root)&(dfs['chain'] == chain), token_type] = 0
                # dfs.to_csv(f'{WD}/connected_wallet/list/root_list.csv', index=False)
                print(f'{tokenSymbol} no {token_type}')
                continue

            df = pd.read_csv(f'{RD}connected_accounts/csv/{root}_{chain}_{token_type}.csv')
            df['layer_one'] = df['to']
            df['insider_contractAddress'] = contractAddress
            df['avg_priceUSD'] = 0
            df['token_number'] = df['value'].astype('float') / 10**df['tokenDecimal']
                
            # Transfer out of the Address
            df = df.loc[df['from'] == root]
            df = df.loc[df['from'] != df['to']]

            # Home Token
            df = df.loc[(df['tokenName'] == tokenName)&
                        (df['tokenSymbol'] == tokenSymbol)&
                        (df['contractAddress'] == contractAddress)]

            # Not Team Finance
            if chain == 'ethereum': 
                df = df.loc[df['to'] != '0xe2fe530c047f2d85298b07d9333c05737f1435fb']
                rpc = 'https://rpc.ankr.com/eth'

            if chain == 'binance': 
                df = df.loc[df['to'] != '0x0c89c0407775dd89b12918b9c0aa42bf96518820']
                rpc = 'https://bscrpc.com'

            if chain == 'avalanche': 
                df = df.loc[df['to'] != '0xe2fe530c047f2d85298b07d9333c05737f1435fb']
                rpc = 'https://api.avax.network/ext/bc/C/rpc'

            if chain == 'fantom': 
                df = df.loc[df['to'] != '0x9f726019452d65a120e1f7ae6b937ee9ebd72440']
                rpc = 'https://rpc.ftm.tools'

            if chain == 'polygon': 
                df = df.loc[df['to'] != '0x3ef7442df454ba6b7c1deec8ddf29cfb2d6e56c7']
                rpc = 'https://polygon-rpc.com'   

            # Not Burn Address
            df = df.loc[(df['to']!= '0x0000000000000000000000000000000000000000')&
                        (df['to']!= '0x000000000000000000000000000000000000dead')
                       ]

            # Not Contract
            df['datetime'] = pd.to_datetime(df['timeStamp'], unit='s', origin='unix')
            df['date'] = df['datetime'].dt.strftime('%Y-%m-%d')
            
            df
            df['date'].unique()
            df.drop_duplicates(['insider_contractAddress', 'date'])
            df.drop_duplicates(['insider_contractAddress', 'date']).shape[0]
            
            for amt_idx, amt_row in df.drop_duplicates(['insider_contractAddress', 'date']).iterrows():
                insider_contractAddress = amt_row['insider_contractAddress']
                timestamp = amt_row['timeStamp']
                date = amt_row['date']
                
                df.loc[(df['insider_contractAddress'] == insider_contractAddress)&
                       (df['date'] == date), 'avg_priceUSD'] = token_dollar_price(contract=insider_contractAddress,
                                                                                   root = root,
                                                                                   chain = chain,
                                                                                   timestamp = timestamp)
            
            df['amountUSD'] = df['avg_priceUSD'] * df['token_number']
            df = df.groupby(['to', 'insider_contractAddress'])['amountUSD'].sum().reset_index()
            df = df.loc[df['amountUSD'] >= 1000]
            
            df.drop_duplicates('to').shape[0]
            num = 0
            
            for df_idx, df_row in df.drop_duplicates('to').iterrows():
                num += 1
                print(f'{num}')
                to = df_row['to']

                w3 = Web3(Web3.HTTPProvider(rpc))
                if w3.eth.getCode(w3.toChecksumAddress(to)).hex() != '0x':
                    df = df.loc[df['to'] != to]

            length = df.shape[0]

            if length != 0:
                df['root'] = root
                df['chain'] = chain
                df['tokenName'] = tokenName
                df['tokenSymbol'] = tokenSymbol
                df['token_type'] = token_type

                supplement.append(df)

            print(f'{root} find {length} connected wallets. {done}/{total}')


            # dfs.loc[(dfs['root'] == root)&(dfs['chain'] == chain), token_type] = length
            # dfs.to_csv(f'{WD}/connected_wallet/list/root_list.csv', index=False)
            
    except Exception as e:
        print(f'{root},{chain},error: {e}')

supplement = pd.concat(supplement)
supplement

blockNumber   timeStamp  \
180       14059084  1642903534   
184       14059281  1642906325   
186       14059435  1642908342   
187       14059435  1642908342   
188       14059435  1642908342   
...            ...         ...   
55147     14075544  1643124585   
55149     14076934  1643142865   
55152     14153994  1644170047   
55214     14630627  1650575895   
55223     14668800  1651093629   

                                                                     hash  \
180    0x8d3f3c3907fba86b271a4890187460ca2637a518c6d787b95bc63ccc94f88929   
184    0x1049e2643a201f6d90a74498c5bce43c2148e0ae8ee4e3ddd6429217e2a62fca   
186    0xefdbf3a4b5622ebaf9690b9e05c583f67de4fbf131ee156b49ac3ea1d54ab78e   
187    0xefdbf3a4b5622ebaf9690b9e05c583f67de4fbf131ee156b49ac3ea1d54ab78e   
188    0xefdbf3a4b5622ebaf9690b9e05c583f67de4fbf131ee156b49ac3ea1d54ab78e   
...                                                                   ...   
55147  0x6c14f4878df5d8897e9684dbc481737f1d99501164c98c88fb41b61b6ad126b0   
55149  0x3790f51b0840933a0f9549ed54c6d34e662f7ddb09c807f6ebe8621b2d9bd723   
55152  0x026985b7784b818f3665619ccfd66b23f2d920dd9e75d982228cb10f5f7cd507   
55214  0x42e41ed25de5f1ec732186d08bdd805def2dca3f128ca4c79653af0935f89f81   
55223  0x5739e5521062ddc90b11cacfa72c2bf2251fb11eb8a50c8966589feadb08c62a   

       nonce  \
180      633   
184      636   
186      637   
187      637   
188      637   
...      ...   
55147   1230   
55149   1233   
55152   1255   
55214   1363   
55223   1380   

                                                                blockHash  \
180    0x73c061edd5ea522216b8a252498ca8ecbceba1f431c613ef65537876496b0922   
184    0xe540083a2452319db0c7848857f657b2cc4b9d9fce4b497834343904791a85d0   
186    0x31d071f751a4b5ef3aa47e01add5224c9c41f92cb07974a82a58b8b7c0d1a66b   
187    0x31d071f751a4b5ef3aa47e01add5224c9c41f92cb07974a82a58b8b7c0d1a66b   
188    0x31d071f751a4b5ef3aa47e01add5224c9c41f92cb07974a82a58b8b7c0d1a66b   
...                                                                   ...   
55147  0x62b57d173bb1ce1124c46e7d338dcd57934eb2843445353398dcebf0bbcd00a3   
55149  0x611dd5b09a034be3793b596d4b4f1e562c549879897cda8618ee5927e44daab9   
55152  0x3648212ed56231e206edb12b3dbfc949a35d0507a6410d8e937148ffadc5ae0c   
55214  0x322451fe0e3b5d563c537b46c728fbf8e3c97e001e5ab0b089919b053e740d64   
55223  0xcc926f8e5d4356530d0b00bd1bd80a8924ef9872c16fc856786a5ef6d88beb43   

                                             from  \
180    0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b   
184    0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b   
186    0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b   
187    0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b   
188    0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b   
...                                           ...   
55147  0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b   
55149  0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b   
55152  0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b   
55214  0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b   
55223  0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b   

                                  contractAddress  \
180    0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
184    0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
186    0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
187    0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
188    0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
...                                           ...   
55147  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
55149  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
55152  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
55214  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
55223  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   

                                               to                   value  \
180    0xca7c2771d248dcbe09eabe0ce57a62e18da178c0    34002181796426716354   
184    0xca7c2771d248dcbe09eabe0ce57a62e18da178c0    32550517466766699770   
186    0x4264ad7beb6a1445099e584b185a3d290e824304 

array(['2022-01-23', '2022-01-24', '2022-01-25', '2022-02-06',
       '2022-04-21', '2022-04-27'], dtype=object)

blockNumber   timeStamp  \
180       14059084  1642903534   
55041     14069433  1643042004   
55147     14075544  1643124585   
55152     14153994  1644170047   
55214     14630627  1650575895   
55223     14668800  1651093629   

                                                                     hash  \
180    0x8d3f3c3907fba86b271a4890187460ca2637a518c6d787b95bc63ccc94f88929   
55041  0x37b0097e6fe6f74e575dc6d41e650c64a265de92be86077beb6a34ff301d0228   
55147  0x6c14f4878df5d8897e9684dbc481737f1d99501164c98c88fb41b61b6ad126b0   
55152  0x026985b7784b818f3665619ccfd66b23f2d920dd9e75d982228cb10f5f7cd507   
55214  0x42e41ed25de5f1ec732186d08bdd805def2dca3f128ca4c79653af0935f89f81   
55223  0x5739e5521062ddc90b11cacfa72c2bf2251fb11eb8a50c8966589feadb08c62a   

       nonce  \
180      633   
55041   1212   
55147   1230   
55152   1255   
55214   1363   
55223   1380   

                                                                blockHash  \
180    0x73c061edd5ea522216b8a252498ca8ecbceba1f431c613ef65537876496b0922   
55041  0xe48e451b8921e7aabdd5a1e195bd38e3f8f959199decbaeb3b53db4eda3b54d7   
55147  0x62b57d173bb1ce1124c46e7d338dcd57934eb2843445353398dcebf0bbcd00a3   
55152  0x3648212ed56231e206edb12b3dbfc949a35d0507a6410d8e937148ffadc5ae0c   
55214  0x322451fe0e3b5d563c537b46c728fbf8e3c97e001e5ab0b089919b053e740d64   
55223  0xcc926f8e5d4356530d0b00bd1bd80a8924ef9872c16fc856786a5ef6d88beb43   

                                             from  \
180    0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b   
55041  0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b   
55147  0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b   
55152  0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b   
55214  0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b   
55223  0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b   

                                  contractAddress  \
180    0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
55041  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
55147  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
55152  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
55214  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
55223  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   

                                               to                   value  \
180    0xca7c2771d248dcbe09eabe0ce57a62e18da178c0    34002181796426716354   
55041  0x8c0b03e05fa6160be40d886d128c61975c1f4400        1953982003748072   
55147  0xb54113aa49b8406fb6992a79cc27c81e9d1c9628  1249670061814621110216   
55152  0xd152f549545093347a162dce210e7293f1452150       62525979338259492   
55214  0x0f9ec5a42e94003e49ab8f79f5e051a2ea5d8c22         350000000000000   
55223  0xb54113aa49b8406fb6992a79cc27c81e9d1c9628    50000000000000000000   

      tokenName tokenSymbol  tokenDecimal  transactionIndex      gas  \
180       FLOKI       FLOKI             9                60   352860   
55041     FLOKI       FLOKI             9                76  2994834   
55147     FLOKI       FLOKI             9               333  3838366   
55152     FLOKI       FLOKI             9               330   249589   
55214     FLOKI       FLOKI             9               123   131419   
55223     FLOKI       FLOKI             9                34   105805   

           gasPrice  gasUsed  cumulativeGasUsed       input  confirmations  \
180    217659183148   264666            3575079  deprecated        1342083   
55041  184636213259  2714036            9568384  deprecated        1331741   
55147  108243768359  2556111           23769419  deprecated        1325630   
55152  103316762107   212463           21845168  deprecated        1247180   
55214   62938696694    84567           13476945  deprecated         770547   
55223   69345509980    67491           14029976  deprecated         732374   

                                        layer_one  \
180    0xca7c2771d248dcbe09eabe0ce57a62e18da178c0   
55041  0x8c0b03e05fa6160be40d886d128c61975c1f4400   
55147  0xb54113aa49b8406fb6992a79cc27c81e9d1c9628   
55152  0xd152f549545093347a

6

9545

...

blockNumber   timeStamp  \
1         26188468  1647866914   
2         26243245  1647987509   
3         26342027  1648204187   
20621     26456126  1648460851   
20622     26512290  1648584902   
20624     26701093  1649000831   
20625     26747318  1649104965   
20626     26777806  1649171913   
20629     27873185  1651577920   

                                                                     hash  \
1      0x6a78fdf4462f49a80cda6ef92b5f5424577fb32b9c5848b2a5ab47dd806ee3bd   
2      0x76c1b23e6ba4a4e49a68e41c7b5bbc25db59f48ee3dfb71d89c4339c37f7c6d1   
3      0x3cb328d5bace8265fbc044afe492a60e6fa1023975114aaa1c808e1fb485e423   
20621  0x3b41afeef68524b97ddf9f087d019a2d17dd49cac9cc67aa5a675bee7ebb765e   
20622  0xd3ca4511a976b04fac71a60330f6e99e4daf6edcd951152da2c34ed12e98ac5f   
20624  0x2d00a2d403c4cc2197440bc029720d7314e5625bf2b594ba5b51dfae63cbd073   
20625  0x58e1d58aca6066a8596bc8f6ed19d54adf8f4f3cfaf19b3dc34c9f309aac6af8   
20626  0xcc75ff2ef8ed28b6e7065ab45da52f2e287203b307007824f1a2ae1306e2cec8   
20629  0x7387f22ad6431464c0b5ea03ec6727ef3b0f0d075d6b66e2c543910f8f9d679e   

       nonce  \
1          3   
2          4   
3          7   
20621    115   
20622    116   
20624    118   
20625    119   
20626    120   
20629    126   

                                                                blockHash  \
1      0xd3443d4dcb2ff3f60ac0b7354509ac8e5aab9f7ce5ef7a0ff5336a6e8e731b6a   
2      0xf28319eee53398f7d771291d38635722c18d41b72a57c38a9e99ecdb12a116f6   
3      0x6d34a51a3c93f1caa3a345569536967dd0655a12f8fe06582dd5e0370a0e34fd   
20621  0x46031bb31e7c8d0d90646ab6037934105db6d2b1d92b87e2620050170cf65c06   
20622  0x6f523b558159943fab5e49d640e4fae0639786fab09297d590f78d65c589c641   
20624  0xcc05c0dfbb2004c2a31ebebb177d21ba6971a07674d02193f5527d2886baed4f   
20625  0xcb0a2770b70c83231a9749fa7543373b991084b5785351c7214b42d7a220c5b7   
20626  0x26ff44f5ab231a6fc1aadab7912a6d030c7c75c9af41eeef2164758d9835896a   
20629  0xf792b6f2ee1cb83a73385c51abf1b3091c2aca9b0ead1f2c664d9985852c459c   

                                             from  \
1      0x129f027a491d96abced68cc30976797a42987303   
2      0x129f027a491d96abced68cc30976797a42987303   
3      0x129f027a491d96abced68cc30976797a42987303   
20621  0x129f027a491d96abced68cc30976797a42987303   
20622  0x129f027a491d96abced68cc30976797a42987303   
20624  0x129f027a491d96abced68cc30976797a42987303   
20625  0x129f027a491d96abced68cc30976797a42987303   
20626  0x129f027a491d96abced68cc30976797a42987303   
20629  0x129f027a491d96abced68cc30976797a42987303   

                                  contractAddress  \
1      0x8f006d1e1d9dc6c98996f50a4c810f17a47fbf19   
2      0x8f006d1e1d9dc6c98996f50a4c810f17a47fbf19   
3      0x8f006d1e1d9dc6c98996f50a4c810f17a47fbf19   
20621  0x8f006d1e1d9dc6c98996f50a4c810f17a47fbf19   
20622  0x8f006d1e1d9dc6c98996f50a4c810f17a47fbf19   
20624  0x8f006d1e1d9dc6c98996f50a4c810f17a47fbf19   
20625  0x8f006d1e1d9dc6c98996f50a4c810f17a47fbf19   
20626  0x8f006d1e1d9dc6c98996f50a4c810f17a47fbf19   
20629  0x8f006d1e1d9dc6c98996f50a4c810f17a47fbf19   

                                               to  \
1      0xfbf09458731c8927766e8d301195d324ba1804b3   
2      0xcb5147c09521b44195b1a0d1876dbf12de7fa8fe   
3      0x1edb83d8288f886d8b3d24f4118e762be3c629cd   
20621  0x687cb60ff514bddf165b14eb7d28f517fa79ed56   
20622  0x84ed758f73c994d61b4a119c06700889c8463f8b   
20624  0x703934a9f7691a4e8949573c40326c8f99a98875   
20625  0x5168b18c1ec6f9ca95af4afae94c8f9662345822   
20626  0x4c2c06e540356b55a2b2babe8a2df13d0a0a7aa6   
20629  0x366ce50bf1d668e3f62a6e3460833af06b1f565a   

                               value      tokenName tokenSymbol  tokenDecimal  \
1           568860000000000000000000  Pleasure Coin        NSFW            18   
2       1700000000000000000000000000  Pleasure Coin        NSFW            18   
3        135920206872694000000000000  Pleasure Coin        NSFW            18   
20621    200000000000000000000000000  Pleasure

9

0

0x129f027a491d96abced68cc30976797a42987303 find 0 connected wallets. 14807/14807


to  \
21   0x000ddd8f0d3deefcbf0b6f9d14b2507dabb99a0f   
25   0x000f6f65dcb7bf0f11c924fb62be537631e280a4   
30   0x00135f983b7c9b7878891c4f2851ea94a08901fb   
32   0x0015eef4843d91d1dc6c52869e8dcf1ae4acad1b   
35   0x001ad98be26f2bdb70a074c1e3d48c96d9d8055f   
..                                          ...   
478  0xfc5737a0fe325d6b2e0c9dc2ac1d81f549fd662c   
479  0xfd5d6417fdcf02f0627aafa9e594a67d4485642d   
480  0xfdf8c05e47dee0f39a29ea262ae0465ee7dad283   
481  0xfe4e81fba38a36f418c42416cc53363a0ddf69b5   
482  0xff0db9ea65862c6f4b097fefab2d81345d289088   

                        insider_contractAddress     amountUSD  \
21   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e  52234.150552   
25   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   6028.360391   
30   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   1628.372959   
32   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   2339.822375   
35   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   6860.089697   
..                                          ...           ...   
478  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   3886.487689   
479  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   9900.999599   
480  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   6132.663923   
481  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   2640.266560   
482  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   2640.266560   

                                           root     chain  \
21   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
25   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
30   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
32   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
35   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
..                                          ...       ...   
478  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
479  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
480  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
481  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
482  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   

                   tokenName tokenSymbol    token_type  
21                     FLOKI       FLOKI  normal_token  
25                     FLOKI       FLOKI  normal_token  
30                     FLOKI       FLOKI  normal_token  
32                     FLOKI       FLOKI  normal_token  
35                     FLOKI       FLOKI  normal_token  
..                       ...         ...           ...  
478  CryptoBlades KING Token        KING  normal_token  
479  CryptoBlades KING Token        KING  normal_token  
480  CryptoBlades KING Token        KING  normal_token  
481  CryptoBlades KING Token        KING  normal_token  
482  CryptoBlades KING Token        KING  normal_token  

[13106 rows x 8 columns]

In [323]:
supplement_to = supplement
supplement_to

to  \
21   0x000ddd8f0d3deefcbf0b6f9d14b2507dabb99a0f   
25   0x000f6f65dcb7bf0f11c924fb62be537631e280a4   
30   0x00135f983b7c9b7878891c4f2851ea94a08901fb   
32   0x0015eef4843d91d1dc6c52869e8dcf1ae4acad1b   
35   0x001ad98be26f2bdb70a074c1e3d48c96d9d8055f   
..                                          ...   
478  0xfc5737a0fe325d6b2e0c9dc2ac1d81f549fd662c   
479  0xfd5d6417fdcf02f0627aafa9e594a67d4485642d   
480  0xfdf8c05e47dee0f39a29ea262ae0465ee7dad283   
481  0xfe4e81fba38a36f418c42416cc53363a0ddf69b5   
482  0xff0db9ea65862c6f4b097fefab2d81345d289088   

                        insider_contractAddress     amountUSD  \
21   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e  52234.150552   
25   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   6028.360391   
30   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   1628.372959   
32   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   2339.822375   
35   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   6860.089697   
..                                          ...           ...   
478  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   3886.487689   
479  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   9900.999599   
480  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   6132.663923   
481  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   2640.266560   
482  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   2640.266560   

                                           root     chain  \
21   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
25   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
30   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
32   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
35   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
..                                          ...       ...   
478  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
479  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
480  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
481  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
482  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   

                   tokenName tokenSymbol    token_type  
21                     FLOKI       FLOKI  normal_token  
25                     FLOKI       FLOKI  normal_token  
30                     FLOKI       FLOKI  normal_token  
32                     FLOKI       FLOKI  normal_token  
35                     FLOKI       FLOKI  normal_token  
..                       ...         ...           ...  
478  CryptoBlades KING Token        KING  normal_token  
479  CryptoBlades KING Token        KING  normal_token  
480  CryptoBlades KING Token        KING  normal_token  
481  CryptoBlades KING Token        KING  normal_token  
482  CryptoBlades KING Token        KING  normal_token  

[13106 rows x 8 columns]

### From

In [325]:
dfs = pd.read_csv(f'{WD}/connected_wallet/list/root_list.csv')

done = dfs.loc[(dfs['normal_token'] != -1)&(dfs['nft_token'] != -1)].shape[0]
total = dfs.shape[0]
supplement = []
    
for idx, row in dfs.loc[(dfs['normal_token'] == -1)|(dfs['nft_token'] == -1)].iterrows():
    done += 1
    root = row['root']
    chain = row['chain']
    tokenName = row['tokenName']
    tokenSymbol = row['tokenSymbol']
    contractAddress = row['contractAddress']

    lst = pd.read_csv(f'{RD}connected_accounts/list/root_{chain}_list.csv')
    
    try:
        
        for token_type in ['normal_token']:
            if lst.loc[lst['root'] == root, token_type].values[0] == 0: 
                dfs.loc[(dfs['root'] == root)&(dfs['chain'] == chain), token_type] = 0
                # dfs.to_csv(f'{WD}/connected_wallet/list/root_list.csv', index=False)
                print(f'{tokenSymbol} no {token_type}')
                continue

            df = pd.read_csv(f'{RD}connected_accounts/csv/{root}_{chain}_{token_type}.csv')
            df['layer_one'] = df['from']
            df['insider_contractAddress'] = contractAddress
            df['avg_priceUSD'] = 0
            df['token_number'] = df['value'].astype('float') / 10**df['tokenDecimal']
                
            # Transfer out of the Address
            df = df.loc[df['to'] == root]
            df = df.loc[df['from'] != df['to']]

            # Home Token
            df = df.loc[(df['tokenName'] == tokenName)&
                        (df['tokenSymbol'] == tokenSymbol)&
                        (df['contractAddress'] == contractAddress)]

            # Not Team Finance
            if chain == 'ethereum': 
                df = df.loc[df['from'] != '0xe2fe530c047f2d85298b07d9333c05737f1435fb']
                rpc = 'https://rpc.ankr.com/eth'

            if chain == 'binance': 
                df = df.loc[df['from'] != '0x0c89c0407775dd89b12918b9c0aa42bf96518820']
                rpc = 'https://bscrpc.com'

            if chain == 'avalanche': 
                df = df.loc[df['from'] != '0xe2fe530c047f2d85298b07d9333c05737f1435fb']
                rpc = 'https://api.avax.network/ext/bc/C/rpc'

            if chain == 'fantom': 
                df = df.loc[df['from'] != '0x9f726019452d65a120e1f7ae6b937ee9ebd72440']
                rpc = 'https://rpc.ftm.tools'

            if chain == 'polygon': 
                df = df.loc[df['from'] != '0x3ef7442df454ba6b7c1deec8ddf29cfb2d6e56c7']
                rpc = 'https://polygon-rpc.com'   

            # Not Burn Address
            df = df.loc[(df['from']!= '0x0000000000000000000000000000000000000000')&
                        (df['from']!= '0x000000000000000000000000000000000000dead')
                       ]

            # Not Contract
            df['datetime'] = pd.to_datetime(df['timeStamp'], unit='s', origin='unix')
            df['date'] = df['datetime'].dt.strftime('%Y-%m-%d')
            
            df
            df['date'].unique()
            df.drop_duplicates(['insider_contractAddress', 'date'])
            df.drop_duplicates(['insider_contractAddress', 'date']).shape[0]
            
            for amt_idx, amt_row in df.drop_duplicates(['insider_contractAddress', 'date']).iterrows():
                insider_contractAddress = amt_row['insider_contractAddress']
                timestamp = amt_row['timeStamp']
                date = amt_row['date']
                
                df.loc[(df['insider_contractAddress'] == insider_contractAddress)&
                       (df['date'] == date), 'avg_priceUSD'] = token_dollar_price(contract=insider_contractAddress,
                                                                                   root = root,
                                                                                   chain = chain,
                                                                                   timestamp = timestamp)
            
            df['amountUSD'] = df['avg_priceUSD'] * df['token_number']
            df = df.groupby(['from', 'insider_contractAddress'])['amountUSD'].sum().reset_index()
            df = df.loc[df['amountUSD'] >= 1000]
            
            df.drop_duplicates('from').shape[0]
            num = 0
            
            for df_idx, df_row in df.drop_duplicates('from').iterrows():
                num += 1
                print(f'{num}')
                from_ = df_row['from']

                w3 = Web3(Web3.HTTPProvider(rpc))
                if w3.eth.getCode(w3.toChecksumAddress(from_)).hex() != '0x':
                    df = df.loc[df['from'] != from_]

            length = df.shape[0]

            if length != 0:
                df['root'] = root
                df['chain'] = chain
                df['tokenName'] = tokenName
                df['tokenSymbol'] = tokenSymbol
                df['token_type'] = token_type

                supplement.append(df)

            print(f'{root} find {length} connected wallets. {done}/{total}')


            # dfs.loc[(dfs['root'] == root)&(dfs['chain'] == chain), token_type] = length
            # dfs.to_csv(f'{WD}/connected_wallet/list/root_list.csv', index=False)
            
    except Exception as e:
        print(f'{root},{chain},error: {e}')

supplement = pd.concat(supplement)
supplement

blockNumber   timeStamp  \
183       14059246  1642905852   
55156     14227226  1645148806   
55158     14279767  1645852656   
55222     14665987  1651055885   

                                                                     hash  \
183    0xe38c2785db3fa5df04c29d3429bfb2eb67a6bb5f936fe71085ff38ce32ed3d65   
55156  0xc1fba76544ef2074d7cc4285664052876dfb6e41f8ec618e315f6c637cd23ddc   
55158  0xa52a514aaaa1031d3b40d7dadc2303c99271e1160382d777c8c3c8f36b33fa9a   
55222  0x763976e5711156aea5e595b84c1d1cf6d92b4eb33b883ccb3222046cf824dd1c   

       nonce  \
183      635   
55156      6   
55158     10   
55222   1377   

                                                                blockHash  \
183    0xe551c2cbba792a82dd168d4d506b982d373cee3280942191d79c7223ea174ebf   
55156  0xe4ade412a01c0a6502af3ea1a576d223b7c9820585b4044c1fd4e35491e1a44d   
55158  0xee80f0eaff304ba98ee89f0d35c68f0ee6187614ca2171735350cfab91ec699a   
55222  0x6c0b627fb20329eac388761f9c38a46a191155275629a0241ca71aa1c4906d91   

                                             from  \
183    0x7a250d5630b4cf539739df2c5dacb4c659f2488d   
55156  0xb6402d02889afb03345c0805e14bfd29a6ce4bac   
55158  0x7828420dabd5fe2505070819b0f2cde0b3faf9ae   
55222  0x2b9d5c7f2ead1a221d771fb6bb5e35df04d60ab0   

                                  contractAddress  \
183    0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
55156  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
55158  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
55222  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   

                                               to                 value  \
183    0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  31584087742293685464   
55156  0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b      1944169060282928   
55158  0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b       423894025565894   
55222  0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  50000000000000000000   

      tokenName tokenSymbol  tokenDecimal  transactionIndex     gas  \
183       FLOKI       FLOKI             9               132  381129   
55156     FLOKI       FLOKI             9                89  105871   
55158     FLOKI       FLOKI             9                62  105871   
55222     FLOKI       FLOKI             9                88  123930   

           gasPrice  gasUsed  cumulativeGasUsed       input  confirmations  \
183    103910413080   244073           14657454  deprecated        1341922   
55156   40763842446    62735            8174840  deprecated        1173948   
55158   31284290669    62735            6869115  deprecated        1121407   
55222   24000000000   119753           10895356  deprecated         735187   

                                        layer_one  \
183    0x7a250d5630b4cf539739df2c5dacb4c659f2488d   
55156  0xb6402d02889afb03345c0805e14bfd29a6ce4bac   
55158  0x7828420dabd5fe2505070819b0f2cde0b3faf9ae   
55222  0x2b9d5c7f2ead1a221d771fb6bb5e35df04d60ab0   

                          insider_contractAddress  avg_priceUSD  token_number  \
183    0xcf0c122c6b73ff809c693db761e7baebe62b6a2e             0  3.158409e+10   
55156  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e             0  1.944169e+06   
55158  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e             0  4.238940e+05   
55222  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e             0  5.000000e+10   

                 datetime        date  
183   2022-01-23 02:44:12  2022-01-23  
55156 2022-02-18 01:46:46  2022-02-18  
55158 2022-02-26 05:17:36  2022-02-26  
55222 2022-04-27 10:38:05  2022-04-27

array(['2022-01-23', '2022-02-18', '2022-02-26', '2022-04-27'],
      dtype=object)

blockNumber   timeStamp  \
183       14059246  1642905852   
55156     14227226  1645148806   
55158     14279767  1645852656   
55222     14665987  1651055885   

                                                                     hash  \
183    0xe38c2785db3fa5df04c29d3429bfb2eb67a6bb5f936fe71085ff38ce32ed3d65   
55156  0xc1fba76544ef2074d7cc4285664052876dfb6e41f8ec618e315f6c637cd23ddc   
55158  0xa52a514aaaa1031d3b40d7dadc2303c99271e1160382d777c8c3c8f36b33fa9a   
55222  0x763976e5711156aea5e595b84c1d1cf6d92b4eb33b883ccb3222046cf824dd1c   

       nonce  \
183      635   
55156      6   
55158     10   
55222   1377   

                                                                blockHash  \
183    0xe551c2cbba792a82dd168d4d506b982d373cee3280942191d79c7223ea174ebf   
55156  0xe4ade412a01c0a6502af3ea1a576d223b7c9820585b4044c1fd4e35491e1a44d   
55158  0xee80f0eaff304ba98ee89f0d35c68f0ee6187614ca2171735350cfab91ec699a   
55222  0x6c0b627fb20329eac388761f9c38a46a191155275629a0241ca71aa1c4906d91   

                                             from  \
183    0x7a250d5630b4cf539739df2c5dacb4c659f2488d   
55156  0xb6402d02889afb03345c0805e14bfd29a6ce4bac   
55158  0x7828420dabd5fe2505070819b0f2cde0b3faf9ae   
55222  0x2b9d5c7f2ead1a221d771fb6bb5e35df04d60ab0   

                                  contractAddress  \
183    0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
55156  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
55158  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   
55222  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   

                                               to                 value  \
183    0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  31584087742293685464   
55156  0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b      1944169060282928   
55158  0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b       423894025565894   
55222  0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  50000000000000000000   

      tokenName tokenSymbol  tokenDecimal  transactionIndex     gas  \
183       FLOKI       FLOKI             9               132  381129   
55156     FLOKI       FLOKI             9                89  105871   
55158     FLOKI       FLOKI             9                62  105871   
55222     FLOKI       FLOKI             9                88  123930   

           gasPrice  gasUsed  cumulativeGasUsed       input  confirmations  \
183    103910413080   244073           14657454  deprecated        1341922   
55156   40763842446    62735            8174840  deprecated        1173948   
55158   31284290669    62735            6869115  deprecated        1121407   
55222   24000000000   119753           10895356  deprecated         735187   

                                        layer_one  \
183    0x7a250d5630b4cf539739df2c5dacb4c659f2488d   
55156  0xb6402d02889afb03345c0805e14bfd29a6ce4bac   
55158  0x7828420dabd5fe2505070819b0f2cde0b3faf9ae   
55222  0x2b9d5c7f2ead1a221d771fb6bb5e35df04d60ab0   

                          insider_contractAddress  avg_priceUSD  token_number  \
183    0xcf0c122c6b73ff809c693db761e7baebe62b6a2e             0  3.158409e+10   
55156  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e             0  1.944169e+06   
55158  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e             0  4.238940e+05   
55222  0xcf0c122c6b73ff809c693db761e7baebe62b6a2e             0  5.000000e+10   

                 datetime        date  
183   2022-01-23 02:44:12  2022-01-23  
55156 2022-02-18 01:46:46  2022-02-18  
55158 2022-02-26 05:17:36  2022-02-26  
55222 2022-04-27 10:38:05  2022-04-27

4

2

...

blockNumber   timeStamp  \
20627     27399312  1650539690   

                                                                     hash  \
20627  0x772efb528cd8542edd9994c56ef705e56e6a647fd4e4fa63841a049daa3a4ad1   

       nonce  \
20627    121   

                                                                blockHash  \
20627  0xd5d88e9f63e625df69610b8b645df46c66e81c7846648618262b575fa921bc9c   

                                             from  \
20627  0x396974bce48a96fa2728aa64d621874dd7cb0038   

                                  contractAddress  \
20627  0x8f006d1e1d9dc6c98996f50a4c810f17a47fbf19   

                                               to                value  \
20627  0x129f027a491d96abced68cc30976797a42987303  8064516129032258064   

           tokenName tokenSymbol  tokenDecimal  transactionIndex    gas  \
20627  Pleasure Coin        NSFW            18               291  50817   

          gasPrice  gasUsed  cumulativeGasUsed       input  confirmations  \
20627  40699614198    50817           25679294  deprecated        4881439   

                                        layer_one  \
20627  0x396974bce48a96fa2728aa64d621874dd7cb0038   

                          insider_contractAddress  avg_priceUSD  token_number  \
20627  0x8f006d1e1d9dc6c98996f50a4c810f17a47fbf19             0      8.064516   

                 datetime        date  
20627 2022-04-21 11:14:50  2022-04-21

1

0

0x129f027a491d96abced68cc30976797a42987303 find 0 connected wallets. 14807/14807


from  \
0      0xc177a2d6113fb6d07c5552ea47e2b03f80d21211   
1      0x000c4ddb952ebda88806af9203dda58bfddc54ec   
53     0x04d8b6bad14515cab029ec15dd2b6dfd125a0ee1   
249    0x182bf7df80f0488b2bc7e2bfcf508ec7c80d5696   
285    0x1bee2ee60326afc7261e6a6f04fd937ba22bc784   
...                                           ...   
22123  0xdf9eec260da99a01b2b893ac512d05c6fbed83a6   
23001  0xe84638119acd8b7c4c1de08d03027c7a46bd4ae1   
24204  0xf41399aac0d78cc955108e12916204d90faff875   
24938  0xfb29ace7a0d650969ca940ecfb0d904d13ddc23f   
25262  0xfe7e63a00d831a4d195be12e3a8d9c4714c909f2   

                          insider_contractAddress    amountUSD  \
0      0xd64f7b8962ede286ac66e290b5d3e5f8f4e019fb  4035.392544   
1      0xab2392379c1c8876690aebbae735ecc2b465825c  7485.025565   
53     0xab2392379c1c8876690aebbae735ecc2b465825c  1305.452065   
249    0xab2392379c1c8876690aebbae735ecc2b465825c  1062.655973   
285    0xab2392379c1c8876690aebbae735ecc2b465825c  1165.914984   
...                                           ...          ...   
22123  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1684.401378   
23001  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  2561.882619   
24204  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1946.795993   
24938  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1201.676021   
25262  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1498.613957   

                                             root    chain  \
0      0xb12e638ee0226e2352a4f2b9f22c6b2f4b4cdc84  binance   
1      0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
53     0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
249    0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
285    0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
...                                           ...      ...   
22123  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
23001  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
24204  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
24938  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
25262  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   

                     tokenName tokenSymbol    token_type  
0                  MEMetaverse          ME  normal_token  
1                     NFTASCII    NFTASCII  normal_token  
53                    NFTASCII    NFTASCII  normal_token  
249                   NFTASCII    NFTASCII  normal_token  
285                   NFTASCII    NFTASCII  normal_token  
...                        ...         ...           ...  
22123  CryptoBlades KING Token        KING  normal_token  
23001  CryptoBlades KING Token        KING  normal_token  
24204  CryptoBlades KING Token        KING  normal_token  
24938  CryptoBlades KING Token        KING  normal_token  
25262  CryptoBlades KING Token        KING  normal_token  

[794 rows x 8 columns]

In [326]:
supplement_from = supplement
supplement_from

from  \
0      0xc177a2d6113fb6d07c5552ea47e2b03f80d21211   
1      0x000c4ddb952ebda88806af9203dda58bfddc54ec   
53     0x04d8b6bad14515cab029ec15dd2b6dfd125a0ee1   
249    0x182bf7df80f0488b2bc7e2bfcf508ec7c80d5696   
285    0x1bee2ee60326afc7261e6a6f04fd937ba22bc784   
...                                           ...   
22123  0xdf9eec260da99a01b2b893ac512d05c6fbed83a6   
23001  0xe84638119acd8b7c4c1de08d03027c7a46bd4ae1   
24204  0xf41399aac0d78cc955108e12916204d90faff875   
24938  0xfb29ace7a0d650969ca940ecfb0d904d13ddc23f   
25262  0xfe7e63a00d831a4d195be12e3a8d9c4714c909f2   

                          insider_contractAddress    amountUSD  \
0      0xd64f7b8962ede286ac66e290b5d3e5f8f4e019fb  4035.392544   
1      0xab2392379c1c8876690aebbae735ecc2b465825c  7485.025565   
53     0xab2392379c1c8876690aebbae735ecc2b465825c  1305.452065   
249    0xab2392379c1c8876690aebbae735ecc2b465825c  1062.655973   
285    0xab2392379c1c8876690aebbae735ecc2b465825c  1165.914984   
...                                           ...          ...   
22123  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1684.401378   
23001  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  2561.882619   
24204  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1946.795993   
24938  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1201.676021   
25262  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1498.613957   

                                             root    chain  \
0      0xb12e638ee0226e2352a4f2b9f22c6b2f4b4cdc84  binance   
1      0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
53     0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
249    0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
285    0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
...                                           ...      ...   
22123  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
23001  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
24204  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
24938  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
25262  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   

                     tokenName tokenSymbol    token_type  
0                  MEMetaverse          ME  normal_token  
1                     NFTASCII    NFTASCII  normal_token  
53                    NFTASCII    NFTASCII  normal_token  
249                   NFTASCII    NFTASCII  normal_token  
285                   NFTASCII    NFTASCII  normal_token  
...                        ...         ...           ...  
22123  CryptoBlades KING Token        KING  normal_token  
23001  CryptoBlades KING Token        KING  normal_token  
24204  CryptoBlades KING Token        KING  normal_token  
24938  CryptoBlades KING Token        KING  normal_token  
25262  CryptoBlades KING Token        KING  normal_token  

[794 rows x 8 columns]

In [331]:
df1 = supplement_to
df2 = supplement_from

# df1.to_csv(f'{WD}connected_wallet/panel/from_10000.csv', index=False)
# df2.to_csv(f'{WD}connected_wallet/panel/to_10000.csv', index=False)

In [332]:
df1
df2

df1.drop_duplicates(['to', 'insider_contractAddress', 'chain'], inplace=True)
df1 = df1.loc[df1['to']!= '0x0000000000000000000000000000000000000001']

df2.drop_duplicates(['from', 'insider_contractAddress', 'chain'], inplace=True)
df2 = df2.loc[df2['from']!= '0x0000000000000000000000000000000000000001']

df1
df2

to  \
21   0x000ddd8f0d3deefcbf0b6f9d14b2507dabb99a0f   
25   0x000f6f65dcb7bf0f11c924fb62be537631e280a4   
30   0x00135f983b7c9b7878891c4f2851ea94a08901fb   
32   0x0015eef4843d91d1dc6c52869e8dcf1ae4acad1b   
35   0x001ad98be26f2bdb70a074c1e3d48c96d9d8055f   
..                                          ...   
478  0xfc5737a0fe325d6b2e0c9dc2ac1d81f549fd662c   
479  0xfd5d6417fdcf02f0627aafa9e594a67d4485642d   
480  0xfdf8c05e47dee0f39a29ea262ae0465ee7dad283   
481  0xfe4e81fba38a36f418c42416cc53363a0ddf69b5   
482  0xff0db9ea65862c6f4b097fefab2d81345d289088   

                        insider_contractAddress     amountUSD  \
21   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e  52234.150552   
25   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   6028.360391   
30   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   1628.372959   
32   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   2339.822375   
35   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   6860.089697   
..                                          ...           ...   
478  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   3886.487689   
479  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   9900.999599   
480  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   6132.663923   
481  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   2640.266560   
482  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   2640.266560   

                                           root     chain  \
21   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
25   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
30   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
32   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
35   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
..                                          ...       ...   
478  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
479  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
480  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
481  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
482  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   

                   tokenName tokenSymbol    token_type  
21                     FLOKI       FLOKI  normal_token  
25                     FLOKI       FLOKI  normal_token  
30                     FLOKI       FLOKI  normal_token  
32                     FLOKI       FLOKI  normal_token  
35                     FLOKI       FLOKI  normal_token  
..                       ...         ...           ...  
478  CryptoBlades KING Token        KING  normal_token  
479  CryptoBlades KING Token        KING  normal_token  
480  CryptoBlades KING Token        KING  normal_token  
481  CryptoBlades KING Token        KING  normal_token  
482  CryptoBlades KING Token        KING  normal_token  

[13105 rows x 8 columns]

from  \
0      0xc177a2d6113fb6d07c5552ea47e2b03f80d21211   
1      0x000c4ddb952ebda88806af9203dda58bfddc54ec   
53     0x04d8b6bad14515cab029ec15dd2b6dfd125a0ee1   
249    0x182bf7df80f0488b2bc7e2bfcf508ec7c80d5696   
285    0x1bee2ee60326afc7261e6a6f04fd937ba22bc784   
...                                           ...   
22123  0xdf9eec260da99a01b2b893ac512d05c6fbed83a6   
23001  0xe84638119acd8b7c4c1de08d03027c7a46bd4ae1   
24204  0xf41399aac0d78cc955108e12916204d90faff875   
24938  0xfb29ace7a0d650969ca940ecfb0d904d13ddc23f   
25262  0xfe7e63a00d831a4d195be12e3a8d9c4714c909f2   

                          insider_contractAddress    amountUSD  \
0      0xd64f7b8962ede286ac66e290b5d3e5f8f4e019fb  4035.392544   
1      0xab2392379c1c8876690aebbae735ecc2b465825c  7485.025565   
53     0xab2392379c1c8876690aebbae735ecc2b465825c  1305.452065   
249    0xab2392379c1c8876690aebbae735ecc2b465825c  1062.655973   
285    0xab2392379c1c8876690aebbae735ecc2b465825c  1165.914984   
...                                           ...          ...   
22123  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1684.401378   
23001  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  2561.882619   
24204  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1946.795993   
24938  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1201.676021   
25262  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1498.613957   

                                             root    chain  \
0      0xb12e638ee0226e2352a4f2b9f22c6b2f4b4cdc84  binance   
1      0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
53     0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
249    0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
285    0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
...                                           ...      ...   
22123  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
23001  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
24204  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
24938  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
25262  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   

                     tokenName tokenSymbol    token_type  
0                  MEMetaverse          ME  normal_token  
1                     NFTASCII    NFTASCII  normal_token  
53                    NFTASCII    NFTASCII  normal_token  
249                   NFTASCII    NFTASCII  normal_token  
285                   NFTASCII    NFTASCII  normal_token  
...                        ...         ...           ...  
22123  CryptoBlades KING Token        KING  normal_token  
23001  CryptoBlades KING Token        KING  normal_token  
24204  CryptoBlades KING Token        KING  normal_token  
24938  CryptoBlades KING Token        KING  normal_token  
25262  CryptoBlades KING Token        KING  normal_token  

[794 rows x 8 columns]

to  \
21   0x000ddd8f0d3deefcbf0b6f9d14b2507dabb99a0f   
25   0x000f6f65dcb7bf0f11c924fb62be537631e280a4   
30   0x00135f983b7c9b7878891c4f2851ea94a08901fb   
32   0x0015eef4843d91d1dc6c52869e8dcf1ae4acad1b   
35   0x001ad98be26f2bdb70a074c1e3d48c96d9d8055f   
..                                          ...   
478  0xfc5737a0fe325d6b2e0c9dc2ac1d81f549fd662c   
479  0xfd5d6417fdcf02f0627aafa9e594a67d4485642d   
480  0xfdf8c05e47dee0f39a29ea262ae0465ee7dad283   
481  0xfe4e81fba38a36f418c42416cc53363a0ddf69b5   
482  0xff0db9ea65862c6f4b097fefab2d81345d289088   

                        insider_contractAddress     amountUSD  \
21   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e  52234.150552   
25   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   6028.360391   
30   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   1628.372959   
32   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   2339.822375   
35   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   6860.089697   
..                                          ...           ...   
478  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   3886.487689   
479  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   9900.999599   
480  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   6132.663923   
481  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   2640.266560   
482  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   2640.266560   

                                           root     chain  \
21   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
25   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
30   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
32   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
35   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
..                                          ...       ...   
478  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
479  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
480  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
481  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
482  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   

                   tokenName tokenSymbol    token_type  
21                     FLOKI       FLOKI  normal_token  
25                     FLOKI       FLOKI  normal_token  
30                     FLOKI       FLOKI  normal_token  
32                     FLOKI       FLOKI  normal_token  
35                     FLOKI       FLOKI  normal_token  
..                       ...         ...           ...  
478  CryptoBlades KING Token        KING  normal_token  
479  CryptoBlades KING Token        KING  normal_token  
480  CryptoBlades KING Token        KING  normal_token  
481  CryptoBlades KING Token        KING  normal_token  
482  CryptoBlades KING Token        KING  normal_token  

[13105 rows x 8 columns]

from  \
0      0xc177a2d6113fb6d07c5552ea47e2b03f80d21211   
1      0x000c4ddb952ebda88806af9203dda58bfddc54ec   
53     0x04d8b6bad14515cab029ec15dd2b6dfd125a0ee1   
249    0x182bf7df80f0488b2bc7e2bfcf508ec7c80d5696   
285    0x1bee2ee60326afc7261e6a6f04fd937ba22bc784   
...                                           ...   
22123  0xdf9eec260da99a01b2b893ac512d05c6fbed83a6   
23001  0xe84638119acd8b7c4c1de08d03027c7a46bd4ae1   
24204  0xf41399aac0d78cc955108e12916204d90faff875   
24938  0xfb29ace7a0d650969ca940ecfb0d904d13ddc23f   
25262  0xfe7e63a00d831a4d195be12e3a8d9c4714c909f2   

                          insider_contractAddress    amountUSD  \
0      0xd64f7b8962ede286ac66e290b5d3e5f8f4e019fb  4035.392544   
1      0xab2392379c1c8876690aebbae735ecc2b465825c  7485.025565   
53     0xab2392379c1c8876690aebbae735ecc2b465825c  1305.452065   
249    0xab2392379c1c8876690aebbae735ecc2b465825c  1062.655973   
285    0xab2392379c1c8876690aebbae735ecc2b465825c  1165.914984   
...                                           ...          ...   
22123  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1684.401378   
23001  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  2561.882619   
24204  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1946.795993   
24938  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1201.676021   
25262  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1498.613957   

                                             root    chain  \
0      0xb12e638ee0226e2352a4f2b9f22c6b2f4b4cdc84  binance   
1      0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
53     0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
249    0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
285    0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
...                                           ...      ...   
22123  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
23001  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
24204  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
24938  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
25262  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   

                     tokenName tokenSymbol    token_type  
0                  MEMetaverse          ME  normal_token  
1                     NFTASCII    NFTASCII  normal_token  
53                    NFTASCII    NFTASCII  normal_token  
249                   NFTASCII    NFTASCII  normal_token  
285                   NFTASCII    NFTASCII  normal_token  
...                        ...         ...           ...  
22123  CryptoBlades KING Token        KING  normal_token  
23001  CryptoBlades KING Token        KING  normal_token  
24204  CryptoBlades KING Token        KING  normal_token  
24938  CryptoBlades KING Token        KING  normal_token  
25262  CryptoBlades KING Token        KING  normal_token  

[792 rows x 8 columns]

In [334]:
df1.rename(columns={'to':'layer_one'}, inplace=True)
df2.rename(columns={'from':'layer_one'}, inplace=True)
df1
df2

layer_one  \
21   0x000ddd8f0d3deefcbf0b6f9d14b2507dabb99a0f   
25   0x000f6f65dcb7bf0f11c924fb62be537631e280a4   
30   0x00135f983b7c9b7878891c4f2851ea94a08901fb   
32   0x0015eef4843d91d1dc6c52869e8dcf1ae4acad1b   
35   0x001ad98be26f2bdb70a074c1e3d48c96d9d8055f   
..                                          ...   
478  0xfc5737a0fe325d6b2e0c9dc2ac1d81f549fd662c   
479  0xfd5d6417fdcf02f0627aafa9e594a67d4485642d   
480  0xfdf8c05e47dee0f39a29ea262ae0465ee7dad283   
481  0xfe4e81fba38a36f418c42416cc53363a0ddf69b5   
482  0xff0db9ea65862c6f4b097fefab2d81345d289088   

                        insider_contractAddress     amountUSD  \
21   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e  52234.150552   
25   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   6028.360391   
30   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   1628.372959   
32   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   2339.822375   
35   0xcf0c122c6b73ff809c693db761e7baebe62b6a2e   6860.089697   
..                                          ...           ...   
478  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   3886.487689   
479  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   9900.999599   
480  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   6132.663923   
481  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   2640.266560   
482  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   2640.266560   

                                           root     chain  \
21   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
25   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
30   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
32   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
35   0xa99c602037f8e85a44bbe88f3c0ee3af60345b9b  ethereum   
..                                          ...       ...   
478  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
479  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
480  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
481  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   
482  0xd74887812b11d84f9709e2c0c3ed566520613373   binance   

                   tokenName tokenSymbol    token_type  
21                     FLOKI       FLOKI  normal_token  
25                     FLOKI       FLOKI  normal_token  
30                     FLOKI       FLOKI  normal_token  
32                     FLOKI       FLOKI  normal_token  
35                     FLOKI       FLOKI  normal_token  
..                       ...         ...           ...  
478  CryptoBlades KING Token        KING  normal_token  
479  CryptoBlades KING Token        KING  normal_token  
480  CryptoBlades KING Token        KING  normal_token  
481  CryptoBlades KING Token        KING  normal_token  
482  CryptoBlades KING Token        KING  normal_token  

[13105 rows x 8 columns]

layer_one  \
0      0xc177a2d6113fb6d07c5552ea47e2b03f80d21211   
1      0x000c4ddb952ebda88806af9203dda58bfddc54ec   
53     0x04d8b6bad14515cab029ec15dd2b6dfd125a0ee1   
249    0x182bf7df80f0488b2bc7e2bfcf508ec7c80d5696   
285    0x1bee2ee60326afc7261e6a6f04fd937ba22bc784   
...                                           ...   
22123  0xdf9eec260da99a01b2b893ac512d05c6fbed83a6   
23001  0xe84638119acd8b7c4c1de08d03027c7a46bd4ae1   
24204  0xf41399aac0d78cc955108e12916204d90faff875   
24938  0xfb29ace7a0d650969ca940ecfb0d904d13ddc23f   
25262  0xfe7e63a00d831a4d195be12e3a8d9c4714c909f2   

                          insider_contractAddress    amountUSD  \
0      0xd64f7b8962ede286ac66e290b5d3e5f8f4e019fb  4035.392544   
1      0xab2392379c1c8876690aebbae735ecc2b465825c  7485.025565   
53     0xab2392379c1c8876690aebbae735ecc2b465825c  1305.452065   
249    0xab2392379c1c8876690aebbae735ecc2b465825c  1062.655973   
285    0xab2392379c1c8876690aebbae735ecc2b465825c  1165.914984   
...                                           ...          ...   
22123  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1684.401378   
23001  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  2561.882619   
24204  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1946.795993   
24938  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1201.676021   
25262  0x0ccd575bf9378c06f6dca82f8122f570769f00c2  1498.613957   

                                             root    chain  \
0      0xb12e638ee0226e2352a4f2b9f22c6b2f4b4cdc84  binance   
1      0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
53     0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
249    0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
285    0x7bcfffc82a80952d617c4ccd8fcf719fea1d218a  binance   
...                                           ...      ...   
22123  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
23001  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
24204  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
24938  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   
25262  0xd74887812b11d84f9709e2c0c3ed566520613373  binance   

                     tokenName tokenSymbol    token_type  
0                  MEMetaverse          ME  normal_token  
1                     NFTASCII    NFTASCII  normal_token  
53                    NFTASCII    NFTASCII  normal_token  
249                   NFTASCII    NFTASCII  normal_token  
285                   NFTASCII    NFTASCII  normal_token  
...                        ...         ...           ...  
22123  CryptoBlades KING Token        KING  normal_token  
23001  CryptoBlades KING Token        KING  normal_token  
24204  CryptoBlades KING Token        KING  normal_token  
24938  CryptoBlades KING Token        KING  normal_token  
25262  CryptoBlades KING Token        KING  normal_token  

[792 rows x 8 columns]

In [336]:
supplement = []
supplement.append(df1.loc[:, ['layer_one', 'insider_contractAddress', 'chain', 'amountUSD']])
supplement.append(df2.loc[:, ['layer_one', 'insider_contractAddress', 'chain', 'amountUSD']])
supplement = pd.concat(supplement)
supplement

layer_one  \
21     0x000ddd8f0d3deefcbf0b6f9d14b2507dabb99a0f   
25     0x000f6f65dcb7bf0f11c924fb62be537631e280a4   
30     0x00135f983b7c9b7878891c4f2851ea94a08901fb   
32     0x0015eef4843d91d1dc6c52869e8dcf1ae4acad1b   
35     0x001ad98be26f2bdb70a074c1e3d48c96d9d8055f   
...                                           ...   
22123  0xdf9eec260da99a01b2b893ac512d05c6fbed83a6   
23001  0xe84638119acd8b7c4c1de08d03027c7a46bd4ae1   
24204  0xf41399aac0d78cc955108e12916204d90faff875   
24938  0xfb29ace7a0d650969ca940ecfb0d904d13ddc23f   
25262  0xfe7e63a00d831a4d195be12e3a8d9c4714c909f2   

                          insider_contractAddress     chain     amountUSD  
21     0xcf0c122c6b73ff809c693db761e7baebe62b6a2e  ethereum  52234.150552  
25     0xcf0c122c6b73ff809c693db761e7baebe62b6a2e  ethereum   6028.360391  
30     0xcf0c122c6b73ff809c693db761e7baebe62b6a2e  ethereum   1628.372959  
32     0xcf0c122c6b73ff809c693db761e7baebe62b6a2e  ethereum   2339.822375  
35     0xcf0c122c6b73ff809c693db761e7baebe62b6a2e  ethereum   6860.089697  
...                                           ...       ...           ...  
22123  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   binance   1684.401378  
23001  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   binance   2561.882619  
24204  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   binance   1946.795993  
24938  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   binance   1201.676021  
25262  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   binance   1498.613957  

[13897 rows x 4 columns]

In [342]:
df1 = pd.read_csv(f'{WD}connected_wallet/panel/panel_large_amount.csv')
df1
supplement

layer_one  \
0      0x000159831a681a63b01911b9c162fbb8949976ba   
1      0x0007a6a1eae3f82897f92f2e9fc476c4be8d4243   
2      0x0009343103cbe1d0898f6f19f0f9442770d008e4   
3      0x0010af1fef93215f345b3531f8d9a39efec93ffb   
4      0x0017177f12a5b8e8c0f13431f12811f5c523fea1   
...                                           ...   
11136  0xffefe959d8baea028b1697abfc4285028d6ceb10   
11137  0xfff108a0218928e60c3f4446ce3d0c5cea744dbc   
11138  0xfff1814d05218eb88931458d71ec8e5871dcccef   
11139  0xfff758bceb9bbb8828af20d03f4de38e1bd8d817   
11140  0xfffee8042d7c434d34d5533cfc7fcbd5c2caf6c6   

                          insider_contractAddress     chain     amountUSD  
0      0x6670d7d4091d9c2f4fb915291630da9146490681   binance  36469.024594  
1      0xaf1167b1f90e4f27d9f520a4cd3a1e452e011cea   binance   2404.686263  
2      0xbc23833d965632cec84bf98181cb84c31bbdfa94   binance   1356.067500  
3      0x643ecd70611e240259e5974468dad69560c5c892   binance   5986.534576  
4      0x5c28dbdf5351089ca413b4493dd6c6043e44af42  ethereum   1556.044180  
...                                           ...       ...           ...  
11136  0x477bc8d23c634c154061869478bce96be6045d12   binance  39223.044785  
11137  0xd0f4afa85a667d27837e9c07c81169869c16dd16   binance   6532.040391  
11138  0x82c2dec3b294671a8bd37e84188fbd312b0da456  ethereum  27071.640000  
11139  0xbf05279f9bf1ce69bbfed670813b7e431142afa4   binance  49088.964764  
11140  0x6670d7d4091d9c2f4fb915291630da9146490681   binance  36469.024594  

[11141 rows x 4 columns]

layer_one  \
21     0x000ddd8f0d3deefcbf0b6f9d14b2507dabb99a0f   
25     0x000f6f65dcb7bf0f11c924fb62be537631e280a4   
30     0x00135f983b7c9b7878891c4f2851ea94a08901fb   
32     0x0015eef4843d91d1dc6c52869e8dcf1ae4acad1b   
35     0x001ad98be26f2bdb70a074c1e3d48c96d9d8055f   
...                                           ...   
22123  0xdf9eec260da99a01b2b893ac512d05c6fbed83a6   
23001  0xe84638119acd8b7c4c1de08d03027c7a46bd4ae1   
24204  0xf41399aac0d78cc955108e12916204d90faff875   
24938  0xfb29ace7a0d650969ca940ecfb0d904d13ddc23f   
25262  0xfe7e63a00d831a4d195be12e3a8d9c4714c909f2   

                          insider_contractAddress     chain     amountUSD  
21     0xcf0c122c6b73ff809c693db761e7baebe62b6a2e  ethereum  52234.150552  
25     0xcf0c122c6b73ff809c693db761e7baebe62b6a2e  ethereum   6028.360391  
30     0xcf0c122c6b73ff809c693db761e7baebe62b6a2e  ethereum   1628.372959  
32     0xcf0c122c6b73ff809c693db761e7baebe62b6a2e  ethereum   2339.822375  
35     0xcf0c122c6b73ff809c693db761e7baebe62b6a2e  ethereum   6860.089697  
...                                           ...       ...           ...  
22123  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   binance   1684.401378  
23001  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   binance   2561.882619  
24204  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   binance   1946.795993  
24938  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   binance   1201.676021  
25262  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   binance   1498.613957  

[13897 rows x 4 columns]

In [344]:
dfs = []
dfs.append(df1)
dfs.append(supplement)
dfs = pd.concat(dfs)

dfs.to_csv(f'{WD}connected_wallet/panel/panel_complete.csv', index=False)
dfs

layer_one  \
0      0x000159831a681a63b01911b9c162fbb8949976ba   
1      0x0007a6a1eae3f82897f92f2e9fc476c4be8d4243   
2      0x0009343103cbe1d0898f6f19f0f9442770d008e4   
3      0x0010af1fef93215f345b3531f8d9a39efec93ffb   
4      0x0017177f12a5b8e8c0f13431f12811f5c523fea1   
...                                           ...   
22123  0xdf9eec260da99a01b2b893ac512d05c6fbed83a6   
23001  0xe84638119acd8b7c4c1de08d03027c7a46bd4ae1   
24204  0xf41399aac0d78cc955108e12916204d90faff875   
24938  0xfb29ace7a0d650969ca940ecfb0d904d13ddc23f   
25262  0xfe7e63a00d831a4d195be12e3a8d9c4714c909f2   

                          insider_contractAddress     chain     amountUSD  
0      0x6670d7d4091d9c2f4fb915291630da9146490681   binance  36469.024594  
1      0xaf1167b1f90e4f27d9f520a4cd3a1e452e011cea   binance   2404.686263  
2      0xbc23833d965632cec84bf98181cb84c31bbdfa94   binance   1356.067500  
3      0x643ecd70611e240259e5974468dad69560c5c892   binance   5986.534576  
4      0x5c28dbdf5351089ca413b4493dd6c6043e44af42  ethereum   1556.044180  
...                                           ...       ...           ...  
22123  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   binance   1684.401378  
23001  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   binance   2561.882619  
24204  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   binance   1946.795993  
24938  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   binance   1201.676021  
25262  0x0ccd575bf9378c06f6dca82f8122f570769f00c2   binance   1498.613957  

[25038 rows x 4 columns]